# DSI 8 Project 2: Ames Housing Modelling
<a id=intro></a>

In this project, we will use the Ames housing data to create a regression model that predicts the price of houses in Ames, IA.

### Problem Statement
> How should we model and predict sales prices of houses in Ames, IA?

### Executive Summary
>In this project, we investigate what is the best way for us to model and to predict sales prices of houses in Ames, IA.<br/>By drawing different models which predict from different combinations of features, we have settled on a single model with predefined parameters that will provide the best scoring in its predictions.<br/>We find that utilizing Elastic Net Regression as our modelling method, with an alpha parameter of 594.531 and an l1 ratio of 1.0, we obtain the best predictions by modelling over a set of 32 features with the top 3 features being the above grade ground living area, the overall material and finish of the house, and the neighbourhood in which the house is located.

### Conclusions and Recommendations
>We recommend that Elastic Net Regression be used with an alpha parameter of 594.531 and an l1 ratio of 1.0. A set of 32 features should be used as predictors which are found in the 'features.txt' document in our datasets folder.

# Contents
- [Introduction & Summary](#intro)
- [Import and Functions](#import)
- [Data Import and Cleaning](#expl)
    - [Faulty Data](#faulty_data)
    - [Filling NA values](#na_val)
    - [Converting Datatypes](#val_conv)
    - [Feature Name Conversion](#feat_conv)
- [Data Analysis](#anal)
    - [Heatmap](#heatmap)
    - [Pairplot](#pairplot)
    - [One-hot Encoding](#dummies)
- [Modelling](#model)
    - [Splitting and Scaling](#splitscale)
    - [Feature Selection](#FS)
    - [Baseline Model](#linreg)
    - [Regularization](#reg)
        - [Ridge Regularization](#ridge)
        - [Elastic Net Regularization](#enet)
- [Final Model](#finalmodel)
    - [Summary](#summary)
    - [Final Model](#finmod)
- [Prediction](#predict)
    - [Import and Cleaning](#predimp)
    - [Dummies](#predummies)
    - [Prediction](#pred)
- [Postamble](#end)

# Import and Functions
<a id=import></a>

### Imports

In [109]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from scipy import stats
from sklearn.model_selection import train_test_split, KFold, cross_val_score
from sklearn.feature_selection import RFE
from sklearn.linear_model import LinearRegression
from sklearn.linear_model import Ridge
from sklearn.linear_model import RidgeCV
from sklearn.linear_model import Lasso
from sklearn.linear_model import LassoCV
from sklearn.linear_model import ElasticNet
from sklearn.linear_model import ElasticNetCV
from sklearn.preprocessing import StandardScaler, PolynomialFeatures
from sklearn.metrics import r2_score
import seaborn as sns

pd.options.display.max_rows=2000
pd.options.display.max_columns=2000
sns.set_style('whitegrid')

%config InlineBackend.figure_format = 'retina'
%matplotlib inline

plt.style.use('fivethirtyeight')

### User-defined Functions
Functions we created that we will use through this project will be listed here 

The function below used to fill zeroes is used [here](#fill_zeroes2)<a id=fill_zeroes></a>

In [110]:
def fill_zeroes(df):
    fill={'Lot Frontage':69,'Alley':'NA','Mas Vnr Type':'None','Mas Vnr Area':0,'Bsmt Qual':'NA',\
         'Bsmt Cond':'NA','Bsmt Exposure':'NA','BsmtFin Type 1':'NA','BsmtFin Type 2':'NA',\
         'BsmtFin SF 1':0,'BsmtFin SF 2':0,'Bsmt Unf SF':0,'Total Bsmt SF':0,'Bsmt Full Bath':0,'Bsmt Half Bath':0,\
         'Fireplace Qu':0,'Garage Type':'NA','Garage Finish':'NA','Garage Qual':'NA','Garage Cond':'NA',\
         'Garage Yr Blt':1978,'Garage Cars':0,'Garage Area':0,'Pool QC':'NA','Fence':'NA','Misc Feature':'NA'}
    df.fillna(value=fill,inplace=True)
    return None

The function below used to convert datatypes is used [here](#data_conv2)<a id=data_conv></a>

In [111]:
def data_conv(df):
    df[['PID','MS SubClass']]=df[['PID','MS SubClass']].astype(str)
    replace={'Lot Shape':{'Reg':3,'IR1':2,'IR2':1,'IR3':0},\
            'Utilities':{'AllPub':3,'NoSewr':2,'NoSeWa':1,'ELO':0},\
            'Land Slope':{'Gtl':2,'Mod':1,'Sev':0},\
            'Exter Qual':{'Ex':4,'Gd':3,'TA':2,'Fa':1,'Po':0},\
            'Exter Cond':{'Ex':4,'Gd':3,'TA':2,'Fa':1,'Po':0},\
            'Bsmt Qual':{'Ex':5,'Gd':4,'TA':3,'Fa':2,'Po':1,'NA':0},\
            'Bsmt Cond':{'Ex':5,'Gd':4,'TA':3,'Fa':2,'Po':1,'NA':0},\
            'Bsmt Exposure':{'Gd':4,'Av':3,'Mn':2,'No':1,'NA':0},\
            'BsmtFin Type 1':{'GLQ':6,'ALQ':5,'BLQ':4,'Rec':3,'LwQ':2,'Unf':1,'NA':0},\
            'BsmtFin Type 2':{'GLQ':6,'ALQ':5,'BLQ':4,'Rec':3,'LwQ':2,'Unf':1,'NA':0},\
            'Heating QC':{'Ex':4,'Gd':3,'TA':2,'Fa':1,'Po':0},\
            'Electrical':{'SBrkr':4,'FuseA':3,'FuseF':2,'FuseP':1,'Mix':0},\
            'Kitchen Qual':{'Ex':4,'Gd':3,'TA':2,'Fa':1,'Po':0},\
            'Functional':{'Typ':7,'Min1':6,'Min2':5,'Mod':4,'Maj1':3,'Maj2':2,'Sev':1,'Sal':0},\
            'Fireplace Qu':{'Ex':5,'Gd':4,'TA':3,'Fa':2,'Po':1,'NA':0},\
            'Garage Finish':{'Fin':3,'RFn':2,'Unf':1,'NA':0},\
            'Garage Qual':{'Ex':5,'Gd':4,'TA':3,'Fa':2,'Po':1,'NA':0},\
            'Garage Cond':{'Ex':5,'Gd':4,'TA':3,'Fa':2,'Po':1,'NA':0},\
            'Paved Drive':{'Y':2,'P':1,'N':0},\
            'Pool QC':{'Ex':4,'Gd':3,'TA':2,'Fa':1,'NA':0},\
            'Fence':{'GdPrv':4,'MnPrv':3,'GdWo':2,'MnWw':1,'NA':0}}
    df.replace(replace,inplace=True,method=None)
    return None

The function below used to obtain adjusted $R^2$ scores is used [here](#ar2_2)<a id=ar2_1></a>

In [112]:
#function for getting adjusted R^2 score
def ar2_score(X_columns,y,r2):
    n=len(y)
    p=len(X_columns)
    ar2=1-(1-r2)*((n-1)/(n-p-1))
    return ar2

The function below used to obtain a list of $R^2$ scores for a list of additional features added is used [here](#r2_list2)<a id=r2_list1></a>

In [113]:
#function for getting R^2 for a list of features
def r2_list(X_columns,X,y,method):
    flist=[]
    rlist=[]
    for i in X_columns:
        flist.append(i)
        r2=cross_val_score(method,X[flist],y,cv=3).mean()
        rlist.append(r2)
    return rlist

The function below used to obtain a list of adjusted $R^2$ scores for a list of additional features added is used [here](#ar2_list2)<a id=ar2_list1></a>

In [114]:
#function for getting adjusted R^2 for a list of features
def ar2_list(X_columns,X,y,method):
    flist=[]
    arlist=[]
    for i in X_columns:
        flist.append(i)
        r2=cross_val_score(method,X[flist],y,cv=3).mean()
        ar2=ar2_score(flist,y,r2)
        arlist.append(ar2)
    return arlist

# Data Import and Cleaning<a id = expl></a>
We import and clean our training data in this section

In [293]:
#Import data
df = pd.read_csv(r'..\datasets\train.csv',index_col='Id')

In [294]:
#Check all available features and cross refer to original data dictionary
df.columns

Index(['PID', 'MS SubClass', 'MS Zoning', 'Lot Frontage', 'Lot Area', 'Street',
       'Alley', 'Lot Shape', 'Land Contour', 'Utilities', 'Lot Config',
       'Land Slope', 'Neighborhood', 'Condition 1', 'Condition 2', 'Bldg Type',
       'House Style', 'Overall Qual', 'Overall Cond', 'Year Built',
       'Year Remod/Add', 'Roof Style', 'Roof Matl', 'Exterior 1st',
       'Exterior 2nd', 'Mas Vnr Type', 'Mas Vnr Area', 'Exter Qual',
       'Exter Cond', 'Foundation', 'Bsmt Qual', 'Bsmt Cond', 'Bsmt Exposure',
       'BsmtFin Type 1', 'BsmtFin SF 1', 'BsmtFin Type 2', 'BsmtFin SF 2',
       'Bsmt Unf SF', 'Total Bsmt SF', 'Heating', 'Heating QC', 'Central Air',
       'Electrical', '1st Flr SF', '2nd Flr SF', 'Low Qual Fin SF',
       'Gr Liv Area', 'Bsmt Full Bath', 'Bsmt Half Bath', 'Full Bath',
       'Half Bath', 'Bedroom AbvGr', 'Kitchen AbvGr', 'Kitchen Qual',
       'TotRms AbvGrd', 'Functional', 'Fireplaces', 'Fireplace Qu',
       'Garage Type', 'Garage Yr Blt', 'Garage Finish'

In [117]:
df.head(5)

PID  MS SubClass MS Zoning  Lot Frontage  Lot Area Street Alley  \
Id                                                                           
109  533352170           60        RL           NaN     13517   Pave   NaN   
544  531379050           60        RL          43.0     11492   Pave   NaN   
153  535304180           20        RL          68.0      7922   Pave   NaN   
318  916386060           60        RL          73.0      9802   Pave   NaN   
255  906425045           50        RL          82.0     14235   Pave   NaN   

    Lot Shape Land Contour Utilities Lot Config Land Slope Neighborhood  \
Id                                                                        
109       IR1          Lvl    AllPub    CulDSac        Gtl       Sawyer   
544       IR1          Lvl    AllPub    CulDSac        Gtl      SawyerW   
153       Reg          Lvl    AllPub     Inside        Gtl        NAmes   
318       Reg          Lvl    AllPub     Inside        Gtl       Timber   
255       IR1          Lvl    AllPub     Inside        Gtl      SawyerW   

    Condition 1 Condition 2 Bldg Type House Style  Overall Qual  Overall Cond  \
Id                                                                              
109        RRAe        Norm      1Fam      2Story             6             8   
544        Norm        Norm      1Fam      2Story             7             5   
153        Norm        Norm      1Fam      1Story             5             7   
318        Norm        Norm      1Fam      2Story             5             5   
255        Norm        Norm      1Fam      1.5Fin             6             8   

     Year Built  Year Remod/Add Roof Style Roof Matl Exterior 1st  \
Id                                                                  
109        1976            2005      Gable   CompShg      HdBoard   
544        1996            1997      Gable   CompShg      VinylSd   
153        1953            2007      Gable   CompShg      VinylSd   
318        2006            2007      Gable   CompShg      VinylSd   
255        1900            1993      Gable   CompShg      Wd Sdng   

    Exterior 2nd Mas Vnr Type  Mas Vnr Area Exter Qual Exter Cond Foundation  \
Id                                                                             
109      Plywood      BrkFace         289.0         Gd         TA     CBlock   
544      VinylSd      BrkFace         132.0         Gd         TA      PConc   
153      VinylSd         None           0.0         TA         Gd     CBlock   
318      VinylSd         None           0.0         TA         TA      PConc   
255      Plywood         None           0.0         TA         TA      PConc   

    Bsmt Qual Bsmt Cond Bsmt Exposure BsmtFin Type 1  BsmtFin SF 1  \
Id                                                                   
109        TA        TA            No            GLQ         533.0   
544        Gd        TA            No            GLQ         637.0   
153        TA        TA            No            GLQ         731.0   
318        Gd        TA            No            Unf           0.0   
255        Fa        Gd            No            Unf           0.0   

    BsmtFin Type 2  BsmtFin SF 2  Bsmt Unf SF  Total Bsmt SF Heating  \
Id                                                                     
109            Unf           0.0        192.0          725.0    GasA   
544            Unf           0.0        276.0          913.0    GasA   
153            Unf           0.0        326.0         1057.0    GasA   
318            Unf           0.0        384.0          384.0    GasA   
255            Unf           0.0        676.0          676.0    GasA   

    Heating QC Central Air Electrical  1st Flr SF  2nd Flr SF  \
Id                                                              
109         Ex           Y      SBrkr         725         754   
544         Ex           Y      SBrkr         913        1209   
153         TA           Y      SBrkr        1057           0   
318 

### We look for faulty data in this subsection <a id=faulty_data></a>

In [118]:
df.describe().T

count          mean           std          min          25%  \
PID              2051.0  7.135900e+08  1.886918e+08  526301100.0  528458140.0   
MS SubClass      2051.0  5.700878e+01  4.282422e+01         20.0         20.0   
Lot Frontage     1721.0  6.905520e+01  2.326065e+01         21.0         58.0   
Lot Area         2051.0  1.006521e+04  6.742489e+03       1300.0       7500.0   
Overall Qual     2051.0  6.112140e+00  1.426271e+00          1.0          5.0   
Overall Cond     2051.0  5.562165e+00  1.104497e+00          1.0          5.0   
Year Built       2051.0  1.971709e+03  3.017789e+01       1872.0       1953.5   
Year Remod/Add   2051.0  1.984190e+03  2.103625e+01       1950.0       1964.5   
Mas Vnr Area     2029.0  9.969591e+01  1.749631e+02          0.0          0.0   
BsmtFin SF 1     2050.0  4.423005e+02  4.612041e+02          0.0          0.0   
BsmtFin SF 2     2050.0  4.795902e+01  1.650009e+02          0.0          0.0   
Bsmt Unf SF      2050.0  5.677283e+02  4.449548e+02          0.0        220.0   
Total Bsmt SF    2050.0  1.057988e+03  4.494107e+02          0.0        793.0   
1st Flr SF       2051.0  1.164488e+03  3.964469e+02        334.0        879.5   
2nd Flr SF       2051.0  3.293291e+02  4.256710e+02          0.0          0.0   
Low Qual Fin SF  2051.0  5.512921e+00  5.106887e+01          0.0          0.0   
Gr Liv Area      2051.0  1.499330e+03  5.004478e+02        334.0       1129.0   
Bsmt Full Bath   2049.0  4.275256e-01  5.226732e-01          0.0          0.0   
Bsmt Half Bath   2049.0  6.344558e-02  2.517052e-01          0.0          0.0   
Full Bath        2051.0  1.577279e+00  5.492794e-01          0.0          1.0   
Half Bath        2051.0  3.710385e-01  5.010427e-01          0.0          0.0   
Bedroom AbvGr    2051.0  2.843491e+00  8.266183e-01          0.0          2.0   
Kitchen AbvGr    2051.0  1.042906e+00  2.097900e-01          0.0          1.0   
TotRms AbvGrd    2051.0  6.435885e+00  1.560225e+00          2.0          5.0   
Fireplaces       2051.0  5.909313e-01  6.385163e-01          0.0          0.0   
Garage Yr Blt    1937.0  1.978708e+03  2.544109e+01       1895.0       1961.0   
Garage Cars      2050.0  1.776585e+00  7.645374e-01          0.0          1.0   
Garage Area      2050.0  4.736717e+02  2.159346e+02          0.0        319.0   
Wood Deck SF     2051.0  9.383374e+01  1.285494e+02          0.0          0.0   
Open Porch SF    2051.0  4.755680e+01  6.674724e+01          0.0          0.0   
Enclosed Porch   2051.0  2.257192e+01  5.984511e+01          0.0          0.0   
3Ssn Porch       2051.0  2.591419e+00  2.522961e+01          0.0          0.0   
Screen Porch     2051.0  1.651146e+01  5.737420e+01          0.0          0.0   
Pool Area        2051.0  2.397855e+00  3.778257e+01          0.0          0.0   
Misc Val         2051.0  5.157435e+01  5.733940e+02          0.0          0.0   
Mo Sold          2051.0  6.219893e+00  2.744736e+00          1.0          4.0   
Yr Sold          2051.0  2.007776e+03  1.312014e+00       2006.0       2007.0   
SalePrice        2051.0  1.814697e+05  7.925866e+04      12789.0     129825.0   

                         50%           75%          max  
PID              535453200.0  9.071801e+08  924152030.0  
MS SubClass             50.0  7.000000e+01        190.0  
Lot Frontage            68.0  8.000000e+01        313.0  
Lot Area              9430.0  1.151350e+04     159000.0  
Overall Qual             6.0  7.000000e+00         10.0  
Overall Cond             5.0  6.000000e+00          9.0  
Year Built            1974.0  2.001000e+03       2010.0  
Year Remod/Add        1993.0  2.004000e+03       2010.0  
Mas Vnr Area             0.0  1.610000e+02       1600.0  
BsmtFin SF 1           368.0  7.337500e+02       5644.0  
BsmtFin SF 2             0.0  0.000000e+00       1474.0  
Bsmt Unf SF            474.5  8.110000e+02       2336.0  
Total Bsmt SF          994.5  1.318750e+03       6110.0  
1st Flr SF            1093.0  1.405000e+03    

On cursory analysis, all data seems to be reasonable with the exception of the following:<br/>

|Feature|Issue|
|---|---|
|Bedroom AbvGr|Some houses have 0 bedrooms, we will check if this is reasonable.|
|Garage Yr Blt|The maximum value of this feature is 2207 indicating this garage was built in the future. We shall check if this is justified.|
|Misc Val|The maximum value of this feature is quite high compared to its mean. We shall check if this is justified.|

---

In [119]:
df[['Bedroom AbvGr']].sort_values('Bedroom AbvGr').T

Id             2523  2724  1000  1386  2119  2540  2252  666   367   1601  \
Bedroom AbvGr     0     0     0     0     0     1     1     1     1     1   

Id             1180  1350  1360  908   242   802   366   1469  2006  230   \
Bedroom AbvGr     1     1     1     1     1     1     1     1     1     1   

Id             1162  301   269   2290  246   1073  2914  819   2881  2844  \
Bedroom AbvGr     1     1     1     1     1     1     1     1     1     1   

Id             299   2803  2793  1948  2257  2429  472   2309  1181  2654  \
Bedroom AbvGr     1     1     1     1     1     1     1     1     1     1   

Id             2242  1391  1598  800   105   108   1179  1470  709   766   \
Bedroom AbvGr     1     1     1     1     1     1     1     1     1     1   

Id             470   1642  2158  879   2600  878   1902  1854  1071  946   \
Bedroom AbvGr     1     1     1     1     1     1     1     1     1     1   

Id             1635  1393  1949  15    1169  453   2804  303   1255  2505  \
Bedroom AbvGr     1     1     1     1     1     1     1     1     1     1   

Id             983   2408  2727  1841  454   2521  2522  2506  785   2293  \
Bedroom AbvGr     1     1     1     1     1     1     1     1     1     1   

Id             2030  2535  1900  1110  724   1901  2400  1285  2596  2689  \
Bedroom AbvGr     2     2     2     2     2     2     2     2     2     2   

Id             2753  870   1657  1043  2461  155   231   2306  1010  945   \
Bedroom AbvGr     2     2     2     2     2     2     2     2     2     2   

Id             1178  406   462   182   1082  2077  1803  407   2300  1742  \
Bedroom AbvGr     2     2     2     2     2     2     2     2     2     2   

Id             2422  1947  1505  2385  705   727   2245  2612  2861  33    \
Bedroom AbvGr     2     2     2     2     2     2     2     2     2     2   

Id             966   1074  1744  1039  104   747   2894  568   2371  648   \
Bedroom AbvGr     2     2     2     2     2     2     2     2     2     2   

Id             2298  793   809   1528  2262  2585  1300  2622  1549  2231  \
Bedroom AbvGr     2     2     2     2     2     2     2     2     2     2   

Id             2643  1671  78    2111  1280  898   473   2013  2493  2588  \
Bedroom AbvGr     2     2     2     2     2     2     2     2     2     2   

Id             2646  1248  168   1561  244   100   152   225   1903  1275  \
Bedroom AbvGr     2     2     2     2     2     2     2     2     2     2   

Id             2671  177   2927  1067  2261  8     1743  2598  45    920   \
Bedroom AbvGr     2     2     2     2     2     2     2     2     2     2   

Id             1170  9     2068  2255  2686  1339  1036  1330  723   97    \
Bedroom AbvGr     2     2     2     2     2     2     2     2     2     2   

Id             1680  614   677   581   1899  1163  1404  2660  620   1002  \
Bedroom AbvGr     2     2     2     2     2     2     2     2     2     2   

Id             1848  1351  2398  2644  1501  626   2004  2693  463   1603  \
Bedroom AbvGr     2     2     2     2     2     2     2     2     2     2   

Id             1520  2627  1502  1621  1253  2897  2406  2707  664   1640  \
Bedroom AbvGr     2     2     2     2     2     2     2     2     2     2   

Id             1298  249   1719  2404  2200  572   981   2507  1515  1675  \
Bedroom AbvGr     2     2     2     2     2     2     2     2     2     2   

Id             130   2875  2226  1472  1450  2364  1888  2619  50    2651  \
Bedroom AbvGr     2     2     2     2     2     2     2     2     2     2   

Id             396   1053  274   2877  514   1301  2048  425   2883  1221  \
Bedroom AbvGr     2     2     2     2     2     2     2     2     2     2   

Id             2072  99    2050  1869  2601  2599  1015  1264  1972  1978  \
Bedroom AbvGr     2     2     2     2     2     2     2     2     2     2   

Id             2769  1547  645   862   1205  875   679   1690  1861  1288  \
Bedroom AbvGr     2     2     2     2     2     

In [120]:
df.loc[[2523,2724,1000,1386,2119],:]

PID  MS SubClass MS Zoning  Lot Frontage  Lot Area Street Alley  \
Id                                                                            
2523  533350050           20        RL          68.0     50271   Pave   NaN   
2724  905200490           80        RL           NaN     10246   Pave   NaN   
1000  527127140          120        RL          41.0      4923   Pave   NaN   
1386  905200090           90        RL          60.0     12900   Pave   NaN   
2119  906475170           20        RL         155.0     20064   Pave   NaN   

     Lot Shape Land Contour Utilities Lot Config Land Slope Neighborhood  \
Id                                                                         
2523       IR1          Low    AllPub     Inside        Gtl      Veenker   
2724       IR1          Lvl    AllPub    CulDSac        Gtl       Sawyer   
1000       Reg          Lvl    AllPub     Inside        Gtl      StoneBr   
1386       Reg          Lvl    AllPub     Inside        Gtl       Sawyer   
2119       IR1          Low    AllPub     Inside        Sev      ClearCr   

     Condition 1 Condition 2 Bldg Type House Style  Overall Qual  \
Id                                                                 
2523        Norm        Norm      1Fam      1Story             9   
2724        Norm        Norm      1Fam        SLvl             4   
1000        Norm        Norm    TwnhsE      1Story             8   
1386       Feedr        Norm    Duplex      SFoyer             4   
2119        Norm        Norm      1Fam      1Story             8   

      Overall Cond  Year Built  Year Remod/Add Roof Style Roof Matl  \
Id                                                                    
2523             5        1981            1987      Gable   WdShngl   
2724             9        1965            2001      Gable   CompShg   
1000             5        2001            2002      Gable   CompShg   
1386             4        1969            1969      Gable   CompShg   
2119             6        1976            1976       Shed   WdShngl   

     Exterior 1st Exterior 2nd Mas Vnr Type  Mas Vnr Area Exter Qual  \
Id                                                                     
2523      WdShing      Wd Shng         None           0.0         Gd   
2724      VinylSd      VinylSd         None           0.0         TA   
1000      CemntBd      CmentBd         None           0.0         Gd   
1386      Plywood      Plywood         None           0.0         TA   
2119      Wd Sdng      Wd Sdng         None           0.0         Gd   

     Exter Cond Foundation Bsmt Qual Bsmt Cond Bsmt Exposure BsmtFin Type 1  \
Id                                                                            
2523         TA     CBlock        Ex        TA            Gd            GLQ   
2724         Gd     CBlock        TA        Gd            Av            GLQ   
1000         TA      PConc        Ex        TA            Av            GLQ   
1386         TA     CBlock        Gd        TA            Av            GLQ   
2119         TA     CBlock        Gd        Gd            Gd            LwQ   

      BsmtFin SF 1 BsmtFin Type 2  BsmtFin SF 2  Bsmt Unf SF  Total Bsmt SF  \
Id                                                                            
2523        1810.0            Unf           0.0         32.0         1842.0   
2724         648.0            Unf           0.0          0.0          648.0   
1000        1153.0            Unf           0.0        440.0         1593.0   
1386        1198.0            Unf           0.0          0.0         1198.0   
2119          51.0            GLQ         915.0          0.0          966.0   

     Heating Heating QC Central Air Electrical  1st Flr SF  2nd Flr SF  \
Id                                                                       
2523    GasA         Gd           Y      SBrkr        1842           0   
2724    GasA         Ex           Y      SBrkr         960           0   
1000    GasA         Ex           Y      

In [121]:
df.loc[[2540,2252,666],:]

PID  MS SubClass MS Zoning  Lot Frontage  Lot Area Street Alley  \
Id                                                                            
2540  534226060           20        RL          71.0      9230   Pave   NaN   
2252  914460110           20        RL          44.0     12864   Pave   NaN   
666   535383120           30        RL          60.0     10800   Pave  Grvl   

     Lot Shape Land Contour Utilities Lot Config Land Slope Neighborhood  \
Id                                                                         
2540       Reg          Lvl    AllPub     Corner        Gtl        NAmes   
2252       IR1          Lvl    AllPub    CulDSac        Gtl      Mitchel   
666        Reg          Lvl    AllPub     Corner        Gtl      OldTown   

     Condition 1 Condition 2 Bldg Type House Style  Overall Qual  \
Id                                                                 
2540       Feedr        Norm      1Fam      1Story             5   
2252        Norm        Norm      1Fam      1Story             7   
666         Norm        Norm      1Fam      1Story             3   

      Overall Cond  Year Built  Year Remod/Add Roof Style Roof Matl  \
Id                                                                    
2540             8        1965            1998        Hip   CompShg   
2252             5        2002            2002      Gable   CompShg   
666              5        1890            1998      Gable   CompShg   

     Exterior 1st Exterior 2nd Mas Vnr Type  Mas Vnr Area Exter Qual  \
Id                                                                     
2540      MetalSd      MetalSd      BrkFace         166.0         TA   
2252      VinylSd      VinylSd         None           0.0         Gd   
666       VinylSd      VinylSd         None           0.0         TA   

     Exter Cond Foundation Bsmt Qual Bsmt Cond Bsmt Exposure BsmtFin Type 1  \
Id                                                                            
2540         TA     CBlock        TA        TA            Mn            GLQ   
2252         TA      PConc        Gd        TA            No            GLQ   
666          TA     BrkTil        TA        TA            No            Unf   

      BsmtFin SF 1 BsmtFin Type 2  BsmtFin SF 2  Bsmt Unf SF  Total Bsmt SF  \
Id                                                                            
2540         661.0            Unf           0.0        203.0          864.0   
2252        1392.0            Unf           0.0         17.0         1409.0   
666            0.0            Unf           0.0        630.0          630.0   

     Heating Heating QC Central Air Electrical  1st Flr SF  2nd Flr SF  \
Id                                                                       
2540    GasA         Gd           Y      SBrkr        1200           0   
2252    GasA         Ex           Y      SBrkr        1409           0   
666     GasA         TA           Y      FuseA         725           0   

      Low Qual Fin SF  Gr Liv Area  Bsmt Full Bath  Bsmt Half Bath  Full Bath  \
Id                                                                              
2540                0         1200             1.0             0.0          1   
2252                0         1409             1.0             0.0          1   
666                 0          725             0.0             0.0          1   

      Half Bath  Bedroom AbvGr  Kitchen AbvGr Kitchen Qual  TotRms AbvGrd  \
Id                                                                          
2540          1              1              1           Gd              6   
2252          1              1              1           Gd              4   
666           1              1              1           TA              4   

     Functional  Fireplaces Fireplace Qu Garage Type  Garage Yr Blt  \
Id                                                                    
2540        Typ           0          NaN      Detchd         1977.0   
2252     

It seems that looking at houses with id numbers 2540, 2252 and 666, it is common that the total rooms above ground do not match up with the bedrooms above ground feature.<br/>
It seems that 0 bedrooms above grade can be justified with the assumption that the bedrooms in the house are unfit for humans to live in and below grade.

---

In [122]:
df[['Garage Yr Blt']].sort_values('Garage Yr Blt').T

Id               1555    308     2600    2636    807     716     1359    2044  \
Garage Yr Blt  1895.0  1896.0  1900.0  1900.0  1900.0  1910.0  1910.0  1910.0   

Id               1975    1288    2851    2660    203     751     761     752   \
Garage Yr Blt  1910.0  1910.0  1914.0  1914.0  1915.0  1915.0  1915.0  1915.0   

Id               656     2663    2028    1311    913     719     2214    2854  \
Garage Yr Blt  1916.0  1916.0  1916.0  1916.0  1916.0  1917.0  1918.0  1919.0   

Id               1349    2852    1556    1350    708     694     2030    2029  \
Garage Yr Blt  1920.0  1920.0  1920.0  1920.0  1920.0  1920.0  1920.0  1920.0   

Id               2088    725     1295    2240    2189    287     1289    1979  \
Garage Yr Blt  1920.0  1920.0  1920.0  1920.0  1920.0  1920.0  1920.0  1920.0   

Id               205     651     1993    236     2659    2654    2684    924   \
Garage Yr Blt  1920.0  1920.0  1920.0  1920.0  1920.0  1921.0  1921.0  1921.0   

Id               1520    1352    302     2696    2844    2238    2862    2666  \
Garage Yr Blt  1921.0  1922.0  1922.0  1922.0  1922.0  1922.0  1922.0  1923.0   

Id               201     2197    729     730     2723    2691    2595    2836  \
Garage Yr Blt  1923.0  1923.0  1923.0  1923.0  1924.0  1924.0  1924.0  1924.0   

Id               1519    1528    914     2686    1358    2641    2000    739   \
Garage Yr Blt  1925.0  1925.0  1925.0  1925.0  1925.0  1925.0  1926.0  1926.0   

Id               2205    919     2850    2021    1340    911     2212    173   \
Garage Yr Blt  1926.0  1926.0  1926.0  1926.0  1926.0  1926.0  1927.0  1927.0   

Id               759     755     2681    1950    2737    917     182     1316  \
Garage Yr Blt  1927.0  1927.0  1928.0  1928.0  1928.0  1928.0  1928.0  1928.0   

Id               1337    916     2643    2682    1298    1345    184     718   \
Garage Yr Blt  1929.0  1929.0  1930.0  1930.0  1930.0  1930.0  1930.0  1930.0   

Id               2216    2651    1996    2245    1360    1313    748     2032  \
Garage Yr Blt  1930.0  1930.0  1930.0  1930.0  1930.0  1930.0  1930.0  1930.0   

Id               722     200     2202    2664    767     908     1532    2860  \
Garage Yr Blt  1930.0  1930.0  1930.0  1930.0  1930.0  1930.0  1931.0  1931.0   

Id               744     2644    1256    2018    1552    768     1310    2039  \
Garage Yr Blt  1931.0  1932.0  1932.0  1933.0  1934.0  1934.0  1935.0  1935.0   

Id               2603    742     1410    1987    1537    1530    2596    2877  \
Garage Yr Blt  1935.0  1935.0  1935.0  1935.0  1935.0  1936.0  1936.0  1936.0   

Id               2863    734     2677    2704    1223    2045    1534    2694  \
Garage Yr Blt  1936.0  1936.0  1936.0  1936.0  1937.0  1937.0  1937.0  1937.0   

Id               2657    2848    711     746     2209    1362    1339    2703  \
Garage Yr Blt  1938.0  1938.0  1938.0  1938.0  1938.0  1938.0  1939.0  1939.0   

Id               2672    2675    2013    2201    195     2015    1539    1222  \
Garage Yr Blt  1939.0  1939.0  1939.0  1939.0  1939.0  1939.0  1939.0  1939.0   

Id               699     737     657     1346    1533    2011    209     1395  \
Garage Yr Blt  1939.0  1939.0  1939.0  1939.0  1939.0  1939.0  1940.0  1940.0   

Id               799     922     177     2068    926     904     658     1335  \
Garage Yr Blt  1940.0  1940.0  1940.0  1940.0  1940.0  1940.0  1940.0  1940.0   

Id               2047    213     2637    1947    2861    944     2662    909   \
Garage Yr Blt  1940.0  1940.0  1940.0  1940.0  1940.0  1940.0  1940.0  1940.0   

Id               2222    1981    793     696     928     2857    1418    1909  \
Garage Yr Blt  1940.0  1940.0  1941.0  1941.0  1941.0  1941.0  1941.0  1941.0   

Id               284     296     2234    2206    197     2873    921     2734  \
Garage Yr Blt  1941.0  1941.0  1941.0  1941.0  1942.0  1942.0  1942.0  1942.0   

Id               2048    1910    648     1329    897     274     2849    231   \
Garage 

In [123]:
df.loc[[2261]]

PID  MS SubClass MS Zoning  Lot Frontage  Lot Area Street Alley  \
Id                                                                            
2261  916384070           20        RL          68.0      8298   Pave   NaN   

     Lot Shape Land Contour Utilities Lot Config Land Slope Neighborhood  \
Id                                                                         
2261       IR1          HLS    AllPub     Inside        Gtl       Timber   

     Condition 1 Condition 2 Bldg Type House Style  Overall Qual  \
Id                                                                 
2261        Norm        Norm      1Fam      1Story             8   

      Overall Cond  Year Built  Year Remod/Add Roof Style Roof Matl  \
Id                                                                    
2261             5        2006            2007        Hip   CompShg   

     Exterior 1st Exterior 2nd Mas Vnr Type  Mas Vnr Area Exter Qual  \
Id                                                                     
2261      VinylSd      VinylSd          NaN           NaN         Gd   

     Exter Cond Foundation Bsmt Qual Bsmt Cond Bsmt Exposure BsmtFin Type 1  \
Id                                                                            
2261         TA      PConc        Gd        TA            Av            GLQ   

      BsmtFin SF 1 BsmtFin Type 2  BsmtFin SF 2  Bsmt Unf SF  Total Bsmt SF  \
Id                                                                            
2261         583.0            Unf           0.0        963.0         1546.0   

     Heating Heating QC Central Air Electrical  1st Flr SF  2nd Flr SF  \
Id                                                                       
2261    GasA         Ex           Y      SBrkr        1564           0   

      Low Qual Fin SF  Gr Liv Area  Bsmt Full Bath  Bsmt Half Bath  Full Bath  \
Id                                                                              
2261                0         1564             0.0             0.0          2   

      Half Bath  Bedroom AbvGr  Kitchen AbvGr Kitchen Qual  TotRms AbvGrd  \
Id                                                                          
2261          0              2              1           Ex              6   

     Functional  Fireplaces Fireplace Qu Garage Type  Garage Yr Blt  \
Id                                                                    
2261        Typ           1           Gd      Attchd         2207.0   

     Garage Finish  Garage Cars  Garage Area Garage Qual Garage Cond  \
Id                                                                     
2261           RFn          2.0        502.0          TA          TA   

     Paved Drive  Wood Deck SF  Open Porch SF  Enclosed Porch  3Ssn Porch  \
Id                                                                          
2261           Y           132              0               0           0   

      Screen Porch  Pool Area Pool QC Fence Misc Feature  Misc Val  Mo Sold  \
Id                                                                            
2261             0          0     NaN   NaN          NaN         0        9   

      Yr Sold Sale Type  SalePrice  
Id                                  
2261     2007       New     267300

There is only one house with a garage built in the future. Upon checking the house id, it seems that there might have been a typo in the year built as it was a new house sold in 2007, so the likelihood is that the garage year built should have been 2007 instead of 2207.

In [124]:
df.loc[2261,'Garage Yr Blt']=2007

We clean the data and check it again with the .loc function above. The data seems to have been changed appropriately.

---

In [125]:
df[['Misc Val']].sort_values('Misc Val').T

Id        109   716   1689  388   1395  800   376   1533  2286  108   29    \
Misc Val     0     0     0     0     0     0     0     0     0     0     0   

Id        2887  2183  1104  2550  1157  2890  1708  1712  144   2642  2015  \
Misc Val     0     0     0     0     0     0     0     0     0     0     0   

Id        2772  2823  674   1266  2277  1945  2737  1230  2047  1293  768   \
Misc Val     0     0     0     0     0     0     0     0     0     0     0   

Id        1200  792   594   846   66    595   787   2293  2556  701   2190  \
Misc Val     0     0     0     0     0     0     0     0     0     0     0   

Id        74    192   2601  2558  987   1521  1719  1221  766   993   902   \
Misc Val     0     0     0     0     0     0     0     0     0     0     0   

Id        729   268   1766  1968  1915  1778  174   650   2444  1043  1028  \
Misc Val     0     0     0     0     0     0     0     0     0     0     0   

Id        2844  2466  1277  1960  119   2841  478   2795  526   2778  472   \
Misc Val     0     0     0     0     0     0     0     0     0     0     0   

Id        1743  2069  2149  784   463   874   2368  2540  1467  2153  1569  \
Misc Val     0     0     0     0     0     0     0     0     0     0     0   

Id        301   1684  1541  231   461   33    1795  1949  1342  1423  1487  \
Misc Val     0     0     0     0     0     0     0     0     0     0     0   

Id        340   2548  977   1682  2104  55    2002  2596  1006  345   2681  \
Misc Val     0     0     0     0     0     0     0     0     0     0     0   

Id        15    2422  2612  727   1000  2637  1752  2152  344   1828  2044  \
Misc Val     0     0     0     0     0     0     0     0     0     0     0   

Id        1576  1073  2319  2790  1889  363   1218  2674  99    2662  2053  \
Misc Val     0     0     0     0     0     0     0     0     0     0     0   

Id        302   283   2664  417   1472  2406  653   2926  1640  601   2491  \
Misc Val     0     0     0     0     0     0     0     0     0     0     0   

Id        2404  475   940   2296  981   269   2507  2416  2038  1675  130   \
Misc Val     0     0     0     0     0     0     0     0     0     0     0   

Id        2547  197   2091  87    938   2388  1495  1609  2820  2881  1421  \
Misc Val     0     0     0     0     0     0     0     0     0     0     0   

Id        791   2731  558   2057  1839  1948  2226  936   1329  2743  1821  \
Misc Val     0     0     0     0     0     0     0     0     0     0     0   

Id        2536  876   1700  2759  200   348   769   2050  2364  690   1451  \
Misc Val     0     0     0     0     0     0     0     0     0     0     0   

Id        1023  2727  229   2566  476   529   2809  1268  1127  2229  2853  \
Misc Val     0     0     0     0     0     0     0     0     0     0     0   

Id        1690  656   2608  1909  2329  1097  446   1658  1589  1850  1243  \
Misc Val     0     0     0     0     0     0     0     0     0     0     0   

Id        1288  1228  507   862   2840  2097  1978  1401  1902  1547  1185  \
Misc Val     0     0     0     0     0     0     0     0     0     0     0   

Id        2372  2445  2075  2568  1797  1166  1418  579   914   1278  2124  \
Misc Val     0     0     0     0     0     0     0     0     0     0     0   

Id        321   452   2915  1663  672   662   2666  1666  237   2682  1296  \
Misc Val     0     0     0     0     0     0     0     0     0     0     0   

Id        2410  456   1852  1659  1128  910   2282  2490  1194  1913  496   \
Misc Val     0     0     0     0     0     0     0     0     0     0     0   

Id        2107  1260  799   2714  1242  2839  2704  2150  619   209   709   \
Misc Val     0     0     0     0     0     0     0     0     0     0     0   

Id        1332  1011  2348  1058  913   622   1052  1     2014  1305  1519  \
Misc Val     0     0     0     0     0     0     0     0     0     0     0   

Id        1352  1963  1503  2675  1835  2486  1911  272   2521  1699  2911 

It seems that the values are reasonable after checking everything in sorted order.

---

In [126]:
df.nunique()

PID                2051
MS SubClass          16
MS Zoning             7
Lot Frontage        118
Lot Area           1476
Street                2
Alley                 2
Lot Shape             4
Land Contour          4
Utilities             3
Lot Config            5
Land Slope            3
Neighborhood         28
Condition 1           9
Condition 2           8
Bldg Type             5
House Style           8
Overall Qual         10
Overall Cond          9
Year Built          113
Year Remod/Add       61
Roof Style            6
Roof Matl             6
Exterior 1st         15
Exterior 2nd         15
Mas Vnr Type          4
Mas Vnr Area        373
Exter Qual            4
Exter Cond            5
Foundation            6
Bsmt Qual             5
Bsmt Cond             5
Bsmt Exposure         4
BsmtFin Type 1        6
BsmtFin SF 1        821
BsmtFin Type 2        6
BsmtFin SF 2        205
Bsmt Unf SF         967
Total Bsmt SF       892
Heating               5
Heating QC            5
Central Air     

We check the number of unique values in nominal data agains the given data dictionary [here](http://jse.amstat.org/v19n3/decock/DataDocumentation.txt), and we find that all nominal data have equal or less unique values than the possible values given in the dictionary, indicating that the nominal data features *should* have no issues.

---

### Filling NA values <a id=na_val></a>

In [127]:
df.isna().sum()

PID                   0
MS SubClass           0
MS Zoning             0
Lot Frontage        330
Lot Area              0
Street                0
Alley              1911
Lot Shape             0
Land Contour          0
Utilities             0
Lot Config            0
Land Slope            0
Neighborhood          0
Condition 1           0
Condition 2           0
Bldg Type             0
House Style           0
Overall Qual          0
Overall Cond          0
Year Built            0
Year Remod/Add        0
Roof Style            0
Roof Matl             0
Exterior 1st          0
Exterior 2nd          0
Mas Vnr Type         22
Mas Vnr Area         22
Exter Qual            0
Exter Cond            0
Foundation            0
Bsmt Qual            55
Bsmt Cond            55
Bsmt Exposure        58
BsmtFin Type 1       55
BsmtFin SF 1          1
BsmtFin Type 2       56
BsmtFin SF 2          1
Bsmt Unf SF           1
Total Bsmt SF         1
Heating               0
Heating QC            0
Central Air     

In [128]:
df[(df['Mas Vnr Type'].isna())|(df['Mas Vnr Area'].isna())][['Mas Vnr Type','Mas Vnr Area']]

Mas Vnr Type  Mas Vnr Area
Id                             
2393          NaN           NaN
2383          NaN           NaN
539           NaN           NaN
518           NaN           NaN
2824          NaN           NaN
1800          NaN           NaN
1455          NaN           NaN
1120          NaN           NaN
1841          NaN           NaN
1840          NaN           NaN
2230          NaN           NaN
1123          NaN           NaN
1784          NaN           NaN
485           NaN           NaN
1752          NaN           NaN
1185          NaN           NaN
1128          NaN           NaN
1096          NaN           NaN
2261          NaN           NaN
2456          NaN           NaN
1728          NaN           NaN
56            NaN           NaN

Missing values in Veneer Type and Area occur together

In [129]:
df[(df['Bsmt Full Bath'].isna())].loc[:,'Bsmt Full Bath':'Bsmt Half Bath']

Bsmt Full Bath  Bsmt Half Bath
Id                                  
1498             NaN             NaN
1342             NaN             NaN

Missing values in 'Bsmt Full Bath' and 'Bsmt Half Bath' occur together

In [130]:
df[(df['Fireplace Qu'].isna())&(df['Fireplaces']!=0)].loc[:,'Fireplaces':'Fireplace Qu']

Empty DataFrame
Columns: [Fireplaces, Fireplace Qu]
Index: []

All *None* values in 'Fireplace Qu' are for house with 0 fireplaces

In [131]:
df[(df['Garage Type'].isna())|\
   (df['Garage Yr Blt'].isna())|\
   (df['Garage Finish'].isna())|\
   (df['Garage Cars'].isna())|\
   (df['Garage Area'].isna())|\
   (df['Garage Qual'].isna())|\
   (df['Garage Cond'].isna())]\
.loc[:,'Garage Type':'Garage Cond']

Garage Type  Garage Yr Blt Garage Finish  Garage Cars  Garage Area  \
Id                                                                        
2243         NaN            NaN           NaN          0.0          0.0   
330          NaN            NaN           NaN          0.0          0.0   
2278         NaN            NaN           NaN          0.0          0.0   
2235         NaN            NaN           NaN          0.0          0.0   
2084         NaN            NaN           NaN          0.0          0.0   
728          NaN            NaN           NaN          0.0          0.0   
781          NaN            NaN           NaN          0.0          0.0   
1492         NaN            NaN           NaN          0.0          0.0   
1514         NaN            NaN           NaN          0.0          0.0   
216          NaN            NaN           NaN          0.0          0.0   
204          NaN            NaN           NaN          0.0          0.0   
754          NaN            NaN           NaN          0.0          0.0   
698          NaN            NaN           NaN          0.0          0.0   
2745         NaN            NaN           NaN          0.0          0.0   
131          NaN            NaN           NaN          0.0          0.0   
615          NaN            NaN           NaN          0.0          0.0   
2824         NaN            NaN           NaN          0.0          0.0   
2846         NaN            NaN           NaN          0.0          0.0   
943          NaN            NaN           NaN          0.0          0.0   
753          NaN            NaN           NaN          0.0          0.0   
2369         NaN            NaN           NaN          0.0          0.0   
2034         NaN            NaN           NaN          0.0          0.0   
2882         NaN            NaN           NaN          0.0          0.0   
1501         NaN            NaN           NaN          0.0          0.0   
2635         NaN            NaN           NaN          0.0          0.0   
1951         NaN            NaN           NaN          0.0          0.0   
1318         NaN            NaN           NaN          0.0          0.0   
900          NaN            NaN           NaN          0.0          0.0   
1376         NaN            NaN           NaN          0.0          0.0   
1366         NaN            NaN           NaN          0.0          0.0   
187          NaN            NaN           NaN          0.0          0.0   
218          NaN            NaN           NaN          0.0          0.0   
1504         NaN            NaN           NaN          0.0          0.0   
2670         NaN            NaN           NaN          0.0          0.0   
2174         NaN            NaN           NaN          0.0          0.0   
1417         NaN            NaN           NaN          0.0          0.0   
2187         NaN            NaN           NaN          0.0          0.0   
1415         NaN            NaN           NaN          0.0          0.0   
2883         NaN            NaN           NaN          0.0          0.0   
207          NaN            NaN           NaN          0.0          0.0   
1292         NaN            NaN           NaN          0.0          0.0   
2875         NaN            NaN           NaN          0.0          0.0   
1135         NaN            NaN           NaN          0.0          0.0   
172          NaN            NaN           NaN          0.0          0.0   
2471         NaN            NaN           NaN          0.0          0.0   
2621         NaN            NaN           NaN          0.0          0.0   
1600         NaN            NaN           NaN          0.0          0.0   
763          NaN            NaN           NaN          0.0          0.0   
1515         NaN            NaN           NaN          0.0          0.0   
1516         NaN            NaN           NaN          0.0          0.0   
1808         NaN            NaN           NaN          0.0          0.0   
2195         NaN            Na

If any garage features are missing values, they are generally missing them across the whole set of garage features. The only exception is house id 2237, however it is a single datapoint. 

The data dictionary for the original source is found [here](http://jse.amstat.org/v19n3/decock/DataDocumentation.txt).<br/>
After consulting the data dictionary, we have decided to resolve features with NA values in the following manner

|Feature|Resolution|Justification|
|---|---|---|
|Lot Frontage|Fill with mean|Continuous feature with no 0 values, skew is minimal so mean or median filling should be fine|
|Alley|Fill with 'NA'|On observation of the dataset, it is highly likely that the data which was supposed to be input as an 'NA' string was input as null values|
|Mas Vnr Type|Fill with 'None'|On observation of the dataset, it is highly likely that the data which was supposed to be input as a 'None' string was input as null values|
|Mas Vnr Area|Fill with 0|If we fill Vnr Type with 'None', the area should be 0|
|Bsmt Qual, Bsmt Cond, Bsmt Exposure and BsmtFin Type 1 & 2|Fill with NA|On observation of the dataset, it is highly likely that the data which was supposed to be input as an 'NA' string was input as null values|
|BsmtFin SF 1 & 2, Bsmt Unf SF and Total Bsmt SF|Fill with 0|It should be ok to set one datapoint to 0|
|Bsmt Full Bath and Bsmt Half Bath|Fill with 0|Basement details are already missing, as such we set basement baths to 0|
|Fireplace Qu|Fill with 0|Houses with NA for 'Fireplace Qu' have 0 fireplaces|
|Garage Type, Finish, Qual and Cond|Fill with 'NA'|We fill in missing garage info as there being no garage. It should be ok to make the assumption for ~5% of the feature data|
|Garage Yr Built|Fill with mean|We cannot fill with 0s as that will heavily skew the data considering the minimum year is 1895. We can fill with the mean as the skew of the data is minimal|
|Garage Cars and Area|Fill with 0|As we are setting the entries as having no garages, we set the values to 0. It should be ok to make the assumption for ~5% of the feature data|
|Pool QC, Fence and Misc Feature|Fill with 'NA'|On observation of the dataset, it is highly likely that the data which was supposed to be input as an 'NA' string was input as null values|

---

We create a function to fill in missing values for all dataframes in the current format.<br/>
The function is found [here](#fill_zeroes)<a id=fill_zeroes2></a>

In [295]:
fill_zeroes(df)

In [296]:
df.isna().sum()

PID                0
MS SubClass        0
MS Zoning          0
Lot Frontage       0
Lot Area           0
Street             0
Alley              0
Lot Shape          0
Land Contour       0
Utilities          0
Lot Config         0
Land Slope         0
Neighborhood       0
Condition 1        0
Condition 2        0
Bldg Type          0
House Style        0
Overall Qual       0
Overall Cond       0
Year Built         0
Year Remod/Add     0
Roof Style         0
Roof Matl          0
Exterior 1st       0
Exterior 2nd       0
Mas Vnr Type       0
Mas Vnr Area       0
Exter Qual         0
Exter Cond         0
Foundation         0
Bsmt Qual          0
Bsmt Cond          0
Bsmt Exposure      0
BsmtFin Type 1     0
BsmtFin SF 1       0
BsmtFin Type 2     0
BsmtFin SF 2       0
Bsmt Unf SF        0
Total Bsmt SF      0
Heating            0
Heating QC         0
Central Air        0
Electrical         0
1st Flr SF         0
2nd Flr SF         0
Low Qual Fin SF    0
Gr Liv Area        0
Bsmt Full Bat

We have successfully filled all NA values.

---

### Converting datatypes<a id=val_conv></a>

In [134]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2051 entries, 109 to 10
Data columns (total 80 columns):
PID                2051 non-null int64
MS SubClass        2051 non-null int64
MS Zoning          2051 non-null object
Lot Frontage       2051 non-null float64
Lot Area           2051 non-null int64
Street             2051 non-null object
Alley              2051 non-null object
Lot Shape          2051 non-null object
Land Contour       2051 non-null object
Utilities          2051 non-null object
Lot Config         2051 non-null object
Land Slope         2051 non-null object
Neighborhood       2051 non-null object
Condition 1        2051 non-null object
Condition 2        2051 non-null object
Bldg Type          2051 non-null object
House Style        2051 non-null object
Overall Qual       2051 non-null int64
Overall Cond       2051 non-null int64
Year Built         2051 non-null int64
Year Remod/Add     2051 non-null int64
Roof Style         2051 non-null object
Roof Matl          

The following should be converted:

|Feature|Convert to|Reason|
|---|---|---|
|PID|string|Nominal data|
|Ms SubClass|string|Nominal data|
|Lot Shape|int64|Ordinal data|
|Utilites|int64|Ordinal data|
|Land Slope|int64|Ordinal data|
|Exter Qual|int64|Ordinal data|
|Exter Cond|int64|Ordinal data|
|Bsmt Qual|int64|Ordinal data|
|Bsmt Cond|int64|Ordinal data|
|Bsmt Exposure|int64|Ordinal data|
|BsmtFin Type 1 & 2|int64|Ordinal data|
|HeatingQC|int64|Ordinal data|
|Electrical|int64|Ordinal data|
|KitchenQual|int64|Ordinal data|
|Functional|int64|Ordinal data|
|FireplaceQu|int64|Ordinal data|
|Garage Finish|int64|Ordinal data|
|Garage Qual|int64|Ordinal data|
|Garage Cond|int64|Ordinal data|
|Paved Drive|int64|Ordinal data|
|Pool QC|int64|Ordinal data|
|Fence|int64|Ordinal data|

We create a function to convert our datatypes.<br/>
The function is found [here](#data_conv)<a id=data_conv2></a>

In [297]:
data_conv(df)

In [298]:
df[['Lot Shape','Utilities','Land Slope','Exter Qual',\
    'Exter Cond','Bsmt Qual','Bsmt Exposure','BsmtFin Type 1',\
    'BsmtFin Type 2','Heating QC','Electrical','Kitchen Qual',\
    'Functional','Fireplace Qu','Garage Finish','Garage Qual',\
    'Garage Cond','Paved Drive','Pool QC','Fence']].info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2051 entries, 109 to 10
Data columns (total 20 columns):
Lot Shape         2051 non-null int64
Utilities         2051 non-null object
Land Slope        2051 non-null int64
Exter Qual        2051 non-null object
Exter Cond        2051 non-null int64
Bsmt Qual         2051 non-null int64
Bsmt Exposure     2051 non-null int64
BsmtFin Type 1    2051 non-null int64
BsmtFin Type 2    2051 non-null int64
Heating QC        2051 non-null int64
Electrical        2051 non-null int64
Kitchen Qual      2051 non-null object
Functional        2051 non-null int64
Fireplace Qu      2051 non-null object
Garage Finish     2051 non-null int64
Garage Qual       2051 non-null int64
Garage Cond       2051 non-null int64
Paved Drive       2051 non-null int64
Pool QC           2051 non-null int64
Fence             2051 non-null int64
dtypes: int64(16), object(4)
memory usage: 336.5+ KB


In [299]:
display(np.unique(df['Utilities'],return_counts=True))
display(np.unique(df['Exter Qual'],return_counts=True))
display(np.unique(df['Kitchen Qual'],return_counts=True))
display(np.unique(df['Fireplace Qu'],return_counts=True))

(array([1, 2, 3], dtype=object), array([   1,    1, 2049], dtype=int64))

(array([1, 2, 3, 4], dtype=object),
 array([  26, 1247,  697,   81], dtype=int64))

(array([1, 2, 3, 4], dtype=object),
 array([  47, 1047,  806,  151], dtype=int64))

(array([0, 1, 2, 3, 4, 5], dtype=object),
 array([1000,   31,   59,  407,  523,   31], dtype=int64))

The four features of 'Utilities', 'Exter Qual', 'Kitchen Qual' and 'Fireplace Qu' are given as dtype objects even though the values are all integers.<br/> 
We shall convert these features to dtype int.

In [300]:
df[['Utilities','Exter Qual','Kitchen Qual','Fireplace Qu']]=df[['Utilities','Exter Qual','Kitchen Qual','Fireplace Qu']].astype(int)

In [301]:
df[['Utilities','Exter Qual','Kitchen Qual','Fireplace Qu']].info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2051 entries, 109 to 10
Data columns (total 4 columns):
Utilities       2051 non-null int32
Exter Qual      2051 non-null int32
Kitchen Qual    2051 non-null int32
Fireplace Qu    2051 non-null int32
dtypes: int32(4)
memory usage: 48.1 KB


Our data has been successfully converted.

---

### Feature name conversion<a id=feat_conv></a>
We convert all our feature names by replacing spaces and converting all letters to lower case before proceeding, for later ease of access.  

In [302]:
df.columns=map(str.lower,df.columns)
df.columns

Index(['pid', 'ms subclass', 'ms zoning', 'lot frontage', 'lot area', 'street',
       'alley', 'lot shape', 'land contour', 'utilities', 'lot config',
       'land slope', 'neighborhood', 'condition 1', 'condition 2', 'bldg type',
       'house style', 'overall qual', 'overall cond', 'year built',
       'year remod/add', 'roof style', 'roof matl', 'exterior 1st',
       'exterior 2nd', 'mas vnr type', 'mas vnr area', 'exter qual',
       'exter cond', 'foundation', 'bsmt qual', 'bsmt cond', 'bsmt exposure',
       'bsmtfin type 1', 'bsmtfin sf 1', 'bsmtfin type 2', 'bsmtfin sf 2',
       'bsmt unf sf', 'total bsmt sf', 'heating', 'heating qc', 'central air',
       'electrical', '1st flr sf', '2nd flr sf', 'low qual fin sf',
       'gr liv area', 'bsmt full bath', 'bsmt half bath', 'full bath',
       'half bath', 'bedroom abvgr', 'kitchen abvgr', 'kitchen qual',
       'totrms abvgrd', 'functional', 'fireplaces', 'fireplace qu',
       'garage type', 'garage yr blt', 'garage finish'

In [303]:
df.columns=df.columns.str.replace(' ','_')
df.columns

Index(['pid', 'ms_subclass', 'ms_zoning', 'lot_frontage', 'lot_area', 'street',
       'alley', 'lot_shape', 'land_contour', 'utilities', 'lot_config',
       'land_slope', 'neighborhood', 'condition_1', 'condition_2', 'bldg_type',
       'house_style', 'overall_qual', 'overall_cond', 'year_built',
       'year_remod/add', 'roof_style', 'roof_matl', 'exterior_1st',
       'exterior_2nd', 'mas_vnr_type', 'mas_vnr_area', 'exter_qual',
       'exter_cond', 'foundation', 'bsmt_qual', 'bsmt_cond', 'bsmt_exposure',
       'bsmtfin_type_1', 'bsmtfin_sf_1', 'bsmtfin_type_2', 'bsmtfin_sf_2',
       'bsmt_unf_sf', 'total_bsmt_sf', 'heating', 'heating_qc', 'central_air',
       'electrical', '1st_flr_sf', '2nd_flr_sf', 'low_qual_fin_sf',
       'gr_liv_area', 'bsmt_full_bath', 'bsmt_half_bath', 'full_bath',
       'half_bath', 'bedroom_abvgr', 'kitchen_abvgr', 'kitchen_qual',
       'totrms_abvgrd', 'functional', 'fireplaces', 'fireplace_qu',
       'garage_type', 'garage_yr_blt', 'garage_finish'

Before we continue, we will drop the PID feature as it is nominal with unique values for each house which will not be useful to us in our regression analysis. We keep all other nominal features as there is the chance that all these features will be useful in our regression. We will eventually use recursive feature elimination to remove features that are not useful for our model.

In [304]:
df.drop('pid',axis=1,inplace=True)
df.columns

Index(['ms_subclass', 'ms_zoning', 'lot_frontage', 'lot_area', 'street',
       'alley', 'lot_shape', 'land_contour', 'utilities', 'lot_config',
       'land_slope', 'neighborhood', 'condition_1', 'condition_2', 'bldg_type',
       'house_style', 'overall_qual', 'overall_cond', 'year_built',
       'year_remod/add', 'roof_style', 'roof_matl', 'exterior_1st',
       'exterior_2nd', 'mas_vnr_type', 'mas_vnr_area', 'exter_qual',
       'exter_cond', 'foundation', 'bsmt_qual', 'bsmt_cond', 'bsmt_exposure',
       'bsmtfin_type_1', 'bsmtfin_sf_1', 'bsmtfin_type_2', 'bsmtfin_sf_2',
       'bsmt_unf_sf', 'total_bsmt_sf', 'heating', 'heating_qc', 'central_air',
       'electrical', '1st_flr_sf', '2nd_flr_sf', 'low_qual_fin_sf',
       'gr_liv_area', 'bsmt_full_bath', 'bsmt_half_bath', 'full_bath',
       'half_bath', 'bedroom_abvgr', 'kitchen_abvgr', 'kitchen_qual',
       'totrms_abvgrd', 'functional', 'fireplaces', 'fireplace_qu',
       'garage_type', 'garage_yr_blt', 'garage_finish', 'gara

Now that our cleaning and transformation has been done, we save our dataframe as the dataset 'train_cleaned'.

In [143]:
df.to_csv(r'..\datasets\train_cleaned.csv')

---
# Data Analysis <a id=anal></a>

We have a read function here to read our cleaned dataframe for future runs.

In [152]:
df=pd.read_csv(r'..\datasets\train_cleaned.csv',index_col='Id')

In [153]:
df.head()

ms_subclass ms_zoning  lot_frontage  lot_area street alley  lot_shape  \
Id                                                                           
109           60        RL          69.0     13517   Pave   NaN          2   
544           60        RL          43.0     11492   Pave   NaN          2   
153           20        RL          68.0      7922   Pave   NaN          3   
318           60        RL          73.0      9802   Pave   NaN          3   
255           50        RL          82.0     14235   Pave   NaN          2   

    land_contour  utilities lot_config  land_slope neighborhood condition_1  \
Id                                                                            
109          Lvl          3    CulDSac           2       Sawyer        RRAe   
544          Lvl          3    CulDSac           2      SawyerW        Norm   
153          Lvl          3     Inside           2        NAmes        Norm   
318          Lvl          3     Inside           2       Timber        Norm   
255          Lvl          3     Inside           2      SawyerW        Norm   

    condition_2 bldg_type house_style  overall_qual  overall_cond  year_built  \
Id                                                                              
109        Norm      1Fam      2Story             6             8        1976   
544        Norm      1Fam      2Story             7             5        1996   
153        Norm      1Fam      1Story             5             7        1953   
318        Norm      1Fam      2Story             5             5        2006   
255        Norm      1Fam      1.5Fin             6             8        1900   

     year_remod/add roof_style roof_matl exterior_1st exterior_2nd  \
Id                                                                   
109            2005      Gable   CompShg      HdBoard      Plywood   
544            1997      Gable   CompShg      VinylSd      VinylSd   
153            2007      Gable   CompShg      VinylSd      VinylSd   
318            2007      Gable   CompShg      VinylSd      VinylSd   
255            1993      Gable   CompShg      Wd Sdng      Plywood   

    mas_vnr_type  mas_vnr_area  exter_qual  exter_cond foundation  bsmt_qual  \
Id                                                                             
109      BrkFace         289.0           3           2     CBlock          3   
544      BrkFace         132.0           3           2      PConc          4   
153         None           0.0           2           3     CBlock          3   
318         None           0.0           2           2      PConc          4   
255         None           0.0           2           2      PConc          2   

     bsmt_cond  bsmt_exposure  bsmtfin_type_1  bsmtfin_sf_1  bsmtfin_type_2  \
Id                                                                            
109          3              1               6         533.0               1   
544          3              1               6         637.0               1   
153          3              1               6         731.0               1   
318          3              1               1           0.0               1   
255          4              1               1           0.0               1   

     bsmtfin_sf_2  bsmt_unf_sf  total_bsmt_sf heating  heating_qc central_air  \
Id                                                                              
109           0.0        192.0          725.0    GasA           4           Y   
544           0.0        276.0          913.0    GasA           4           Y   
153           0.0        326.0         1057.0    GasA           2           Y   
318           0.0        384.0          384.0    GasA           3           Y   
255           0.0        676.0          676.0    GasA           2           Y   

     electrical  1st_flr_sf  2nd_flr_sf  low_qual_fin_sf  gr_liv_area  \
Id                                                                      
109           4 

### Heatmap<a id=heatmap></a>

Next, we create a heatmap to determine what continuous and ordinal features we may wish to drop.<br/>
The heatmap is saved to our 'pics' folder as 'corr.png' for easier external viewing.

In [145]:
#Create correlation heatmap of all features
fig, ax = plt.subplots(figsize=(60,60))
corr = np.corrcoef(df.corr())
mask = np.zeros_like(corr)
mask[np.triu_indices_from(mask)] = True #Create upper triangular mask
sns.heatmap(df.corr(),linewidths=.5,ax=ax,mask=mask,annot=True,fmt='.2f') #Enable correlation values to 2 d.p.
ax.set_title('Correlation Heatmap')
plt.show()
fig.savefig(r'..\pics\corr.png', format='png')

We investigate all features (not including our target 'sale_price') with a correlation score above 0.7. All scores are greater than -0.7 as such we assume that our features do not have significant negative correlation dependence.

|Feature 1|Feature 2|Corr. Score|Decision|
|---|---|---|---|
|exter_qual|overall_qual|0.74|It is likely that overall quality is highly dependent on exterior quality. As such we choose to drop exterior quality as overall quality should be a sufficient predictor|
|kitchen_qual|exter_qual|0.73|Kitchen, exterior and overall quality seem to be interdependent. As kitchen and overall quality have a correlation score of 0.69, we choose to drop kitchen quality as well|
|bsmtfin_type_1|bsmtfin_sf_1|0.70|The basement rating and its area seem to be related. As such we choose to drop 'bsmtfin_sf_1' as its area can be represented by its rating|
|bsmtfin_type_2|bsmtfin_sf_2|0.78|Similar to the previous case, we choose to drop 'bsmtfin_sf_2'|
|1st_flr_sf|total_bsmt_sf|0.81|The size of the basement is highly correlated to the size of the first floor, and we choose to drop total_bsmt_sf as 1st_flr_sf would serve as a sufficient predictor|
|totrms_abvgrd|gr_liv_area|0.81|The 'total rooms above grade and 'above grade living area' features are highly correlated. We choose to drop 'totrms_abvgrd' as 'gr_liv_area' seems to have a better correlation with sale price|
|fireplace_qu|fireplaces|0.86|Fireplace quality and their quantity are highly correlated. We drop 'fireplaces' as 'fireplace_qu' has a better correlation with sale price|
|garage_yr_blt|year_built|0.79|When houses and garages are built seem to be highly correlated, as such we drop 'garage_yr_blt' as 'year_built has a better correlation with sale price|
|garage_area|garage_cars|0.89|The garage area directly affects the number of cars it can store. We drop 'garage_cars' as the area serves as a sufficient predictor|
|paved_drive|garage_qual|0.95|There is a very high correlation between how the driveway is paved and the quality of the house's garage. We drop 'paved_drive' as 'garage_qual' should serve as a sufficient predictor|
|pool_qc|pool_area|0.87|The quality of the pool and its area are highly correlated. We drop 'pool_area' as 'pool_qc' has a slightly higher correlation with sale price|

Next, we investigate features correlation scores between -0.2 and 0.2 with sale price and decide if they are worth keeping.

|Feature|Corr. Score|Decision|
|---|---|---|
|utilities|0.03|We drop it due to its low correlation|
|land_slope|-0.06|We drop it due to its low correlation|
|overall_cond|-0.10|We make the subjective decision to keep it as domain knowledge tells us that the condition of the residence should affect the sale price. We can observe how useful it is when we perform lasso regression later on|
|exter_cond|0.04|We drop it due to its low correlation|
|bsmtfin_type_2|0.01|We drop it due to its low correlation|
|bsmtfin_sf_2|0.02|We drop it due to its low correlation|
|bsmt_unf_sf|0.19|We drop it due to its low correlation|
|low_qual_fin_sf|-0.04|We drop it due to its low correlation|
|bsmt_half_bath|-0.05|We drop it due to its low correlation|
|bedroom_abvgr|0.14|We drop it due to its low correlation|
|kitchen_abvgr|-0.13|We drop it due to its low correlation|
|functional|0.13|We drop it due to its low correlation|
|enclosed_porch|-0.14|We drop it due to its low correlation|
|3ssn_porch|0.05|We drop it due to its low correlation|
|screen_porch|0.13|We drop it due to its low correlation|
|pool_area|0.02|We drop it due to its low correlation|
|pool_qc|0.03|We drop it due to its low correlation|
|fence|-0.16|We drop it due to its low correlation|
|misc_val|-0.01|We drop it due to its low correlation|
|mo_sold|0.03|We drop it due to its low correlation|
|yr_sold|-0.02|We drop it due to its low correlation|

From our analysis so far, we have decided to drop the following 30 features:<br/>
exter_qual, kitchen_qual, bsmtfin_sf_1, bsmtfin_sf_2, total_bsmt_sf, totrms_abvgrd, fireplaces, garage_yr_blt, garage_cars, paved_drive, pool_area, utilities, land_slope, exter_cond, bsmtfin_type_2, bsmt_unf_sf, low_qual_fin_sf, bsmt_half_bath, bedroom_abvgr, kitchen_abvgr, functional, enclosed_porch, 3ssn_porch, screen_porch, pool_area, pool_qc, fence, misc_val, mo_sold, yr_sold

In [154]:
x='exter_qual, kitchen_qual, bsmtfin_sf_1, bsmtfin_sf_2, total_bsmt_sf, totrms_abvgrd, fireplaces, garage_yr_blt, garage_cars, paved_drive, pool_area, utilities, land_slope, exter_cond, bsmtfin_type_2, bsmt_unf_sf, low_qual_fin_sf, bsmt_half_bath, bedroom_abvgr, kitchen_abvgr, functional, enclosed_porch, 3ssn_porch, screen_porch, pool_area, pool_qc, fence, misc_val, mo_sold, yr_sold'
lst=x.split(', ')
lst

['exter_qual',
 'kitchen_qual',
 'bsmtfin_sf_1',
 'bsmtfin_sf_2',
 'total_bsmt_sf',
 'totrms_abvgrd',
 'fireplaces',
 'garage_yr_blt',
 'garage_cars',
 'paved_drive',
 'pool_area',
 'utilities',
 'land_slope',
 'exter_cond',
 'bsmtfin_type_2',
 'bsmt_unf_sf',
 'low_qual_fin_sf',
 'bsmt_half_bath',
 'bedroom_abvgr',
 'kitchen_abvgr',
 'functional',
 'enclosed_porch',
 '3ssn_porch',
 'screen_porch',
 'pool_area',
 'pool_qc',
 'fence',
 'misc_val',
 'mo_sold',
 'yr_sold']

In [155]:
#we first check if there are any issues with out drop 
df.drop(lst,axis=1).columns

Index(['ms_subclass', 'ms_zoning', 'lot_frontage', 'lot_area', 'street',
       'alley', 'lot_shape', 'land_contour', 'lot_config', 'neighborhood',
       'condition_1', 'condition_2', 'bldg_type', 'house_style',
       'overall_qual', 'overall_cond', 'year_built', 'year_remod/add',
       'roof_style', 'roof_matl', 'exterior_1st', 'exterior_2nd',
       'mas_vnr_type', 'mas_vnr_area', 'foundation', 'bsmt_qual', 'bsmt_cond',
       'bsmt_exposure', 'bsmtfin_type_1', 'heating', 'heating_qc',
       'central_air', 'electrical', '1st_flr_sf', '2nd_flr_sf', 'gr_liv_area',
       'bsmt_full_bath', 'full_bath', 'half_bath', 'fireplace_qu',
       'garage_type', 'garage_finish', 'garage_area', 'garage_qual',
       'garage_cond', 'wood_deck_sf', 'open_porch_sf', 'misc_feature',
       'sale_type', 'saleprice'],
      dtype='object')

In [156]:
df.drop(lst,axis=1,inplace=True)

---
### Pairplot <a id=pairplot></a>

We further examine our data with pairplots.

In [ ]:
g = sns.pairplot(df.drop(df.select_dtypes(['object']), axis=1))
g.savefig(r'..\pics\pairplot.png')

As indicated in the source [data dictionary](http://jse.amstat.org/v19n3/decock/DataDocumentation.txt), we observe some outliers in the plot of 'gr_live_area' against 'sale_price'.<br/>
The following is an excerpt from the dictionary:
>SPECIAL NOTES:
There are 5 observations that an instructor may wish to remove from the data set before giving it to students (a plot of SALE PRICE versus GR LIV AREA will indicate them quickly). Three of them are true outliers (Partial Sales that likely don’t represent actual market values) and two of them are simply unusual sales (very large houses priced relatively appropriately). I would recommend removing any houses with more than 4000 square feet from the data set (which eliminates these 5 unusual observations) before assigning it to students.

We can observe two clear outliers in the plot where large houses are sold for low prices. We keep these two datapoints in building our baseline and observe later if removing these outliers make any improvement to our model.<br/><br/>
From the plots, it seems that 1st_flr_sf and gr_liv_area give us the most homoscedastic fits relative to sale price.<br/>
While overall_qual gives us the best correlation in the heatmap, the variation seems to be heteroscedastic where variation in sale price increases with better overall quality.

---

### One-hot Encoding <a id=dummies></a>
Before we proceed, we one-hot-encode our nominal data.

In [157]:
# Check the output first
pd.get_dummies(df, drop_first=True).head()
# pd.get_dummies(df, drop_first=True).info()

ms_subclass  lot_frontage  lot_area  lot_shape  overall_qual  \
Id                                                                  
109           60          69.0     13517          2             6   
544           60          43.0     11492          2             7   
153           20          68.0      7922          3             5   
318           60          73.0      9802          3             5   
255           50          82.0     14235          2             6   

     overall_cond  year_built  year_remod/add  mas_vnr_area  bsmt_qual  \
Id                                                                       
109             8        1976            2005         289.0          3   
544             5        1996            1997         132.0          4   
153             7        1953            2007           0.0          3   
318             5        2006            2007           0.0          4   
255             8        1900            1993           0.0          2   

     bsmt_cond  bsmt_exposure  bsmtfin_type_1  heating_qc  electrical  \
Id                                                                      
109          3              1               6           4           4   
544          3              1               6           4           4   
153          3              1               6           2           4   
318          3              1               1           3           4   
255          4              1               1           2           4   

     1st_flr_sf  2nd_flr_sf  gr_liv_area  bsmt_full_bath  full_bath  \
Id                                                                    
109         725         754         1479             0.0          2   
544         913        1209         2122             1.0          2   
153        1057           0         1057             1.0          1   
318         744         700         1444             0.0          2   
255         831         614         1445             0.0          2   

     half_bath  fireplace_qu  garage_finish  garage_area  garage_qual  \
Id                                                                      
109          1             0              2        475.0            3   
544          1             3              2        559.0            3   
153          0             0              1        246.0            3   
318          1             0              3        400.0            3   
255          0             0              1        484.0            3   

     garage_cond  wood_deck_sf  open_porch_sf  saleprice  ms_zoning_C (all)  \
Id                                                                            
109            3             0             44     130500                  0   
544            3             0             74     220000                  0   
153            3             0             52     109000                  0   
318            3           100              0     174000                  0   
255            3             0             59     138500                  0   

     ms_zoning_FV  ms_zoning_I (all)  ms_zoning_RH  ms_zoning_RL  \
Id                                                                 
109             0                  0             0             1   
544             0                  0             0             1   
153             0                  0             0             1   
318             0                  0             0             1   
255             0                  0             0             1   

     ms_zoning_RM  street_Pave  alley_Pave  land_contour_HLS  \
Id                                                             
109             0            1           0                 0   
544             0            1           0                 0   
153             0            1           0                 0   
318             0            1           0                 0   
255             0            1           0                 0   



In [158]:
# Create the dataframe
df_dummies = pd.get_dummies(df, drop_first=True)

We save our dummified dataset externally for ease of use for future runs.

In [159]:
df_dummies.to_csv(r'..\datasets\train_drop_dummies.csv')

---
# Modelling <a id=model></a>

We import our dummified dataset for future runs.

In [263]:
df_dummies=pd.read_csv(r'..\datasets\train_drop_dummies.csv',index_col='Id')

In [162]:
df_dummies.head()

ms_subclass  lot_frontage  lot_area  lot_shape  overall_qual  \
Id                                                                  
109           60          69.0     13517          2             6   
544           60          43.0     11492          2             7   
153           20          68.0      7922          3             5   
318           60          73.0      9802          3             5   
255           50          82.0     14235          2             6   

     overall_cond  year_built  year_remod/add  mas_vnr_area  bsmt_qual  \
Id                                                                       
109             8        1976            2005         289.0          3   
544             5        1996            1997         132.0          4   
153             7        1953            2007           0.0          3   
318             5        2006            2007           0.0          4   
255             8        1900            1993           0.0          2   

     bsmt_cond  bsmt_exposure  bsmtfin_type_1  heating_qc  electrical  \
Id                                                                      
109          3              1               6           4           4   
544          3              1               6           4           4   
153          3              1               6           2           4   
318          3              1               1           3           4   
255          4              1               1           2           4   

     1st_flr_sf  2nd_flr_sf  gr_liv_area  bsmt_full_bath  full_bath  \
Id                                                                    
109         725         754         1479             0.0          2   
544         913        1209         2122             1.0          2   
153        1057           0         1057             1.0          1   
318         744         700         1444             0.0          2   
255         831         614         1445             0.0          2   

     half_bath  fireplace_qu  garage_finish  garage_area  garage_qual  \
Id                                                                      
109          1             0              2        475.0            3   
544          1             3              2        559.0            3   
153          0             0              1        246.0            3   
318          1             0              3        400.0            3   
255          0             0              1        484.0            3   

     garage_cond  wood_deck_sf  open_porch_sf  saleprice  ms_zoning_C (all)  \
Id                                                                            
109            3             0             44     130500                  0   
544            3             0             74     220000                  0   
153            3             0             52     109000                  0   
318            3           100              0     174000                  0   
255            3             0             59     138500                  0   

     ms_zoning_FV  ms_zoning_I (all)  ms_zoning_RH  ms_zoning_RL  \
Id                                                                 
109             0                  0             0             1   
544             0                  0             0             1   
153             0                  0             0             1   
318             0                  0             0             1   
255             0                  0             0             1   

     ms_zoning_RM  street_Pave  alley_Pave  land_contour_HLS  \
Id                                                             
109             0            1           0                 0   
544             0            1           0                 0   
153             0            1           0                 0   
318             0            1           0                 0   
255             0            1           0                 0   



### Splitting and Scaling<a id=splitscale></a>
In the following steps, we perform the following:
1. Separate our dataframe into features and our target
2. Create a training and a holdout set (3 to 1 ratio)
3. Scale our data and save the parameters obtained from fitting to our training set

[move forward to Lasso cross validation](#cv1)<a id=cv2></a>

In [264]:
# Create feature and target matrices
features = [col for col in df_dummies.columns if not col == 'saleprice']
X = df_dummies[features]
y = df_dummies['saleprice']

In [265]:
#We perform 4-fold cross validation to find a good random state to use for train_test_split
kf=KFold(n_splits=4, shuffle=True, random_state=555)
lr = LinearRegression()
cross_val_score(lr, X, y, cv=kf)

array([0.83987208, 0.8035334 , 0.8731461 , 0.87150926])

We observe that with a random state of 555, the cross val scores are similar across all 4 folds and our data is well-mixed.

In [266]:
# We create a training and a holdout set
X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=555, shuffle=True) #change the random state if cross validation below is problematic

In [267]:
#Scale data to z-scores
ss = StandardScaler()
X_scaled = ss.fit_transform(X_train) #perform our fit according to our training set
X_sctest = ss.transform(X_test) #transform our test set with parameters obtained from our training set

#Get parameters for future fit
ss_mean=ss.mean_
ss_var=ss.var_

E:\Users\chang\Anaconda3\lib\site-packages\sklearn\preprocessing\data.py:645: DataConversionWarning: Data with input dtype int64, float64 were all converted to float64 by StandardScaler.
  return self.partial_fit(X, y)
E:\Users\chang\Anaconda3\lib\site-packages\sklearn\base.py:464: DataConversionWarning: Data with input dtype int64, float64 were all converted to float64 by StandardScaler.
  return self.fit(X, **fit_params).transform(X)
E:\Users\chang\Anaconda3\lib\site-packages\ipykernel_launcher.py:4: DataConversionWarning: Data with input dtype int64, float64 were all converted to float64 by StandardScaler.
  after removing the cwd from sys.path.


In [167]:
#save our standard scaler transformation parameters
#enable the two lines below to display the mean and variance arrays
# display(ss_mean)
# display(ss_var)
np.savetxt(r'..\datasets\ss_mean.txt',ss_mean)
np.savetxt(r'..\datasets\ss_var.txt',ss_var)

---
### Feature Selection <a id=FS></a>

We first determine the optimum alpha for our Lasso function

In [168]:
optimal_lasso = LassoCV(n_alphas=500, cv=10, verbose=1, n_jobs=-1)
optimal_lasso.fit(X_scaled, y_train)

print('optimal lasso alpha: ' + str(optimal_lasso.alpha_))

[Parallel(n_jobs=-1)]: Using backend ThreadingBackend with 8 concurrent workers.
.......................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................

optimal lasso alpha: 568.0385667755177


[move back to splitting and scaling](#cv2)<a id=cv1></a><br/>
Next, we perform 10-fold cross validation with Lasso to check if our dataset has been well-split 

In [169]:
lasso = Lasso(alpha=optimal_lasso.alpha_) #Set our optimum alpha as the Lasso parameter

lasso_scores = cross_val_score(lasso, X_scaled, y_train, cv=10)

print('lasso cross val scores: ' + str(lasso_scores))
print('lasso cv mean score: ' + str(np.mean(lasso_scores)))

lasso cross val scores: [0.88698619 0.79653195 0.7232056  0.88880594 0.89304608 0.87762365
 0.87678111 0.86032081 0.8851325  0.91393545]
lasso cv mean score: 0.8602369282111759


---
We iterate the above until our cross-val score array gives us largely similar scores throughout.<br/>
We find that 555 is a good random state to set in our train-test-split function above.<br/><br/>
Next, we use our Lasso function to rank the features that predict our target.<br/>We then save it in a list.

In [170]:
lasso.fit(X_scaled, y_train)

lasso_coefs = pd.DataFrame({'variable':X_train.columns,
                            'coef':lasso.coef_,
                            'abs_coef':np.abs(lasso.coef_)})

lasso_coefs.sort_values('abs_coef', inplace=True, ascending=False)

lasso_coefs.head(30)

variable          coef      abs_coef
17            gr_liv_area  24134.744732  24134.744732
4            overall_qual  15943.389729  15943.389729
61   neighborhood_NridgHt   9819.480090   9819.480090
0             ms_subclass  -8926.083779   8926.083779
6              year_built   7371.431790   7371.431790
11          bsmt_exposure   7211.733603   7211.733603
23            garage_area   6911.932425   6911.932425
67   neighborhood_StoneBr   6773.549162   6773.549162
18         bsmt_full_bath   5258.828466   5258.828466
5            overall_cond   5168.196177   5168.196177
8            mas_vnr_area   4720.645569   4720.645569
9               bsmt_qual   4209.076777   4209.076777
60   neighborhood_NoRidge   4151.773643   4151.773643
52   neighborhood_GrnHill   4010.941356   4010.941356
12         bsmtfin_type_1   3760.196710   3760.196710
161         sale_type_New   3718.881023   3718.881023
2                lot_area   3651.779846   3651.779846
21           fireplace_qu   3138.469634   3138.469634
98         roof_style_Hip   3042.373541   3042.373541
66   neighborhood_Somerst   2641.558199   2641.558199
13             heating_qc   2570.317713   2570.317713
105     roof_matl_WdShngl   2482.911083   2482.911083
48   neighborhood_Crawfor   2450.515607   2450.515607
73       condition_1_PosN   2256.597020   2256.597020
108  exterior_1st_BrkFace   2195.722884   2195.722884
36       land_contour_HLS   2081.493447   2081.493447
7          year_remod/add   1790.758518   1790.758518
71       condition_1_Norm   1747.188861   1747.188861
111  exterior_1st_HdBoard  -1746.635447   1746.635447
136    mas_vnr_type_Stone   1544.717584   1544.717584

In [171]:
var100=lasso_coefs.reset_index().loc[0:99,'variable'].tolist()
var100

['gr_liv_area',
 'overall_qual',
 'neighborhood_NridgHt',
 'ms_subclass',
 'year_built',
 'bsmt_exposure',
 'garage_area',
 'neighborhood_StoneBr',
 'bsmt_full_bath',
 'overall_cond',
 'mas_vnr_area',
 'bsmt_qual',
 'neighborhood_NoRidge',
 'neighborhood_GrnHill',
 'bsmtfin_type_1',
 'sale_type_New',
 'lot_area',
 'fireplace_qu',
 'roof_style_Hip',
 'neighborhood_Somerst',
 'heating_qc',
 'roof_matl_WdShngl',
 'neighborhood_Crawfor',
 'condition_1_PosN',
 'exterior_1st_BrkFace',
 'land_contour_HLS',
 'year_remod/add',
 'condition_1_Norm',
 'exterior_1st_HdBoard',
 'mas_vnr_type_Stone',
 'exterior_1st_CemntBd',
 'neighborhood_Edwards',
 'bldg_type_2fmCon',
 'roof_style_Mansard',
 'condition_1_PosA',
 'lot_config_CulDSac',
 'condition_2_PosA',
 'ms_zoning_RM',
 'lot_frontage',
 'foundation_Slab',
 'neighborhood_NWAmes',
 'full_bath',
 'foundation_CBlock',
 'exterior_1st_Wd Sdng',
 'house_style_2.5Unf',
 'condition_1_RRAe',
 '1st_flr_sf',
 'half_bath',
 'bsmt_cond',
 'neighborhood_BrkSide

After creating the list, we calculate the adjusted $R^2$ values for our combinations of features to find the best amount of features for our model.
- <a id=ar2_2></a>We create a function that calculates adjusted $R^2$ scores [here](#ar2_1).<br/>
- <a id=r2_list2></a>We create a function that obtains a list of 𝑅2 scores for a list of additional features added [here](#r2_list1).<br/>
- <a id=ar2_list2></a>We create a function that obtains a list of adjusted 𝑅2 scores for a list of additional features added [here](#ar2_list1).

In [172]:
#We convert our X_scaled array back into a dataframe or manipulation 
X_scaled_df=pd.DataFrame(X_scaled,columns=X_train.columns)
X_scaled_df.head()

ms_subclass  lot_frontage  lot_area  lot_shape  overall_qual  overall_cond  \
0    -0.853345      0.009424  0.152248   0.720527      1.345627     -0.510566   
1     1.487379      0.009424 -0.876199   0.720527     -0.777013      0.383797   
2     0.082945      1.827546  0.536118   0.720527      1.345627     -0.510566   
3    -0.619272      1.474022 -0.200906  -1.069733     -0.777013     -0.510566   
4    -0.853345      0.059928 -0.296649   0.720527     -0.069467      2.172523   

   year_built  year_remod/add  mas_vnr_area  bsmt_qual  bsmt_cond  \
0    1.006445        0.853571     -0.566896   0.562396   0.112562   
1    0.109355       -0.435962     -0.566896   0.562396   0.112562   
2    1.006445        0.853571      0.745811   0.562396   0.112562   
3   -1.718050       -1.629973     -0.566896  -0.563861   0.112562   
4   -0.588382        0.758050      0.428951  -0.563861   0.112562   

   bsmt_exposure  bsmtfin_type_1  heating_qc  electrical  1st_flr_sf  \
0      -0.585884        1.129235    0.879650    0.277856    0.504702   
1      -0.585884        1.129235   -0.154678    0.277856   -0.316683   
2       2.200990        1.129235    0.879650    0.277856    1.354500   
3      -0.585884        0.181220   -1.189007    0.277856    0.011355   
4      -0.585884        0.655227    0.879650    0.277856   -0.290853   

   2nd_flr_sf  gr_liv_area  bsmt_full_bath  full_bath  half_bath  \
0   -0.765477    -0.277557        1.074715  -1.048817   1.266855   
1   -0.765477    -0.921044       -0.829561  -1.048817  -0.739760   
2    0.555017     1.527444        1.074715   0.775934   1.266855   
3   -0.765477    -0.664054       -0.829561  -1.048817  -0.739760   
4   -0.765477    -0.900809        1.074715  -1.048817  -0.739760   

   fireplace_qu  garage_finish  garage_area  garage_qual  garage_cond  \
0      0.690477      -0.795197    -0.243542     0.275241     0.270585   
1     -0.974027      -0.795197     0.130919     0.275241     0.270585   
2      1.800146       1.408429     1.319023     0.275241     0.270585   
3      1.245312      -0.795197     0.112427     0.275241     0.270585   
4     -0.974027       0.306616    -0.853774     0.275241     0.270585   

   wood_deck_sf  open_porch_sf  ms_zoning_C (all)  ms_zoning_FV  \
0     -0.206744       1.768659          -0.092329     -0.221615   
1     -0.722919       0.786687          -0.092329     -0.221615   
2      1.083696       1.233038          -0.092329     -0.221615   
3     -0.722919      -0.701150          -0.092329     -0.221615   
4     -0.722919      -0.701150          -0.092329     -0.221615   

   ms_zoning_I (all)  ms_zoning_RH  ms_zoning_RL  ms_zoning_RM  street_Pave  \
0          -0.025507     -0.080898      0.527703     -0.426811     0.051064   
1          -0.025507     -0.080898     -1.895005      2.342958     0.051064   
2          -0.025507     -0.080898      0.527703     -0.426811     0.051064   
3          -0.025507     -0.080898      0.527703     -0.426811     0.051064   
4          -0.025507     -0.080898      0.527703     -0.426811     0.051064   

   alley_Pave  land_contour_HLS  land_contour_Low  land_contour_Lvl  \
0   -0.161299         -0.201483           -0.1526          0.331162   
1   -0.161299         -0.201483           -0.1526          0.331162   
2   -0.161299         -0.201483           -0.1526          0.331162   
3   -0.161299         -0.201483           -0.1526          0.331162   
4   -0.161299         -0.201483           -0.1526          0.331162   

   lot_config_CulDSac  lot_config_FR2  lot_config_FR3  lot_config_Inside  \
0           -0.260875       -0.185195       -0.076722          -1.607819   
1           -0.260875       -0.185195       -0.076722           0.621961   
2           -0.260875       -0.185195       -0.076722          -1.607819   
3           -0.260875       -0.185195       -0.076722           0.621961   
4           -0.260875       -0.185195       -0.076722           0.621961   

   neighborhood_Blueste  neighborhood_BrDale  neighborhood

In [173]:
#We calculate a list of R-squared values to check against our adjusted R-squared values later. 
r2_list(var100,X_scaled_df,y_train,lasso)

[0.5009885859582475,
 0.7237299379922052,
 0.7437390616014822,
 0.7613453183164908,
 0.7850891045298206,
 0.8094320107426327,
 0.8172722080474486,
 0.8248324224365019,
 0.8333775238409951,
 0.8376827164820861,
 0.8382412224245619,
 0.8390596185271709,
 0.8391139608673036,
 0.8419872717822089,
 0.8418000389840645,
 0.8454522622514334,
 0.84516518439967,
 0.847800303534458,
 0.8503043663517239,
 0.8517365616468261,
 0.8530526577288841,
 0.8535254604127757,
 0.856235232618396,
 0.8553840452320038,
 0.8550267024965934,
 0.8561735537879457,
 0.8560297964252198,
 0.8562487305459113,
 0.8569266501657163,
 0.856275408035465,
 0.8553529574488038,
 0.8551166347952369,
 0.8561685762838384,
 0.855977105087006,
 0.8562073908410976,
 0.8561480192673931,
 0.8564522377527494,
 0.8564619013799671,
 0.8561559872255335,
 0.85679096298704,
 0.856745451774881,
 0.8569066087225329,
 0.8566200969635233,
 0.8564684427128837,
 0.8567718320145903,
 0.8568014562332215,
 0.8537400314400418,
 0.8534457906675396,
 

In [174]:
#We calculate a list of adjusted R-squared values to determine the best amount of features to place in our model.
ar2lst=ar2_list(var100,X_scaled_df,y_train,lasso)
ar2_df=pd.DataFrame([list(X_train.columns.values)[0:100],ar2lst])
ar2_df.T.sort_values(1,ascending=False)

0         1
28     ms_zoning_C (all)  0.854175
22         garage_finish  0.854051
25           garage_cond  0.853699
27         open_porch_sf  0.853581
26          wood_deck_sf  0.853455
29          ms_zoning_FV  0.853414
23           garage_area   0.85309
32          ms_zoning_RL  0.853013
39    lot_config_CulDSac  0.852964
36      land_contour_HLS  0.852911
41        lot_config_FR3  0.852887
34           street_Pave  0.852857
37      land_contour_Low  0.852823
40        lot_config_FR2  0.852819
33          ms_zoning_RM  0.852719
35            alley_Pave  0.852698
24           garage_qual   0.85263
42     lot_config_Inside  0.852493
44   neighborhood_BrDale  0.852452
38      land_contour_Lvl  0.852411
45  neighborhood_BrkSide  0.852384
30     ms_zoning_I (all)  0.852375
43  neighborhood_Blueste  0.852238
31          ms_zoning_RH  0.852036
21          fireplace_qu  0.851398
20             half_bath  0.851017
19             full_bath  0.849782
46  neighborhood_ClearCr  0.849126
53   neighborhood_IDOTRR  0.848794
47  neighborhood_CollgCr  0.848721
50  neighborhood_Gilbert  0.848673
52  neighborhood_GrnHill  0.848606
51   neighborhood_Greens  0.848565
54  neighborhood_Landmrk  0.848443
18        bsmt_full_bath  0.848431
49  neighborhood_Edwards  0.848422
48  neighborhood_Crawfor  0.848392
55  neighborhood_MeadowV  0.848381
56  neighborhood_Mitchel  0.848183
57    neighborhood_NAmes   0.84806
58  neighborhood_NPkVill  0.848004
59   neighborhood_NWAmes  0.847855
60  neighborhood_NoRidge  0.847697
61  neighborhood_NridgHt  0.846911
62  neighborhood_OldTown  0.846837
63    neighborhood_SWISU   0.84675
64   neighborhood_Sawyer  0.846594
65  neighborhood_SawyerW  0.846444
66  neighborhood_Somerst  0.846364
67  neighborhood_StoneBr  0.846327
17           gr_liv_area  0.845997
68   neighborhood_Timber  0.843924
15            1st_flr_sf  0.843827
69  neighborhood_Veenker  0.843767
70     condition_1_Feedr  0.843663
71      condition_1_Norm  0.843498
16            2nd_flr_sf  0.843433
72      condition_1_PosA  0.843315
73      condition_1_PosN  0.843148
74      condition_1_RRAe  0.843086
75      condition_1_RRAn  0.842695
76      condition_1_RRNe  0.842329
77      condition_1_RRNn  0.841566
78     condition_2_Feedr  0.841385
79      condition_2_Norm  0.841128
80      condition_2_PosA   0.84103
81      condition_2_PosN  0.840707
13            heating_qc  0.840535
14            electrical  0.840241
82      condition_2_RRAe  0.840216
83      condition_2_RRAn  0.840082
84      condition_2_RRNn  0.839882
85      bldg_type_2fmCon  0.839733
86      bldg_type_Duplex  0.839623
87       bldg_type_Twnhs  0.839394
88      bldg_type_TwnhsE  0.839283
89    house_style_1.5Unf  0.839172
90    house_style_1Story  0.839061
91    house_style_2.5Fin  0.838658
92    house_style_2.5Unf  0.838546
93    house_style_2Story  0.838374
94    house_style_SFoyer  0.838274
95      house_style_SLvl   0.83814
96      roof_style_Gable  0.838008
97    roof_style_Gambrel  0.837897
11         bsmt_exposure  0.837793
12        bsmtfin_type_1  0.837742
98        roof_style_Hip  0.837724
99    roof_style_Mansard  0.837611
10             bsmt_cond  0.837075
9              bsmt_qual   0.83662
8           mas_vnr_area  0.832396
7         year_remod/add  0.823916
6             year_built  0.816436
5           overall_cond  0.808685
4           overall_qual  0.784388
3              lot_shape  0.760723
2               lot_area  0.743238
1           lot_frontage   0.72337
0            ms_subclass  0.500664

The addition of features improves the adjusted $R^2$ score up to a point. The best adjusted $R^2$ score is 0.8541 for 28 combined features up to ms_zoning_C (all). 

In [175]:
#Convert our scaled X_test array into a dataframe for further manipulation
X_sctest_df=pd.DataFrame(X_sctest,columns=X_train.columns)

In [176]:
len(X_sctest_df)

513

In [179]:
lassor2=[]
lassoar2=[]
n=len(X_sctest_df)
for i in range(1,101):
    lasso.fit(X_scaled_df[var100[0:i]].values,y_train)
    r2=lasso.score(X_sctest_df[var100[0:i]].values,y_test)
    lassor2.append(r2)
    lassoar2.append(1-(1-r2)*((n-1)/(n-i-1)))

In [180]:
lassodf=pd.DataFrame([list(X_train.columns.values)[0:100],lassor2,lassoar2])
lassodf.T.sort_values(2,ascending=False)

0         1         2
36      land_contour_HLS  0.853399  0.841979
37      land_contour_Low  0.853654  0.841922
32          ms_zoning_RL  0.851989  0.841792
35            alley_Pave  0.852484  0.841328
33          ms_zoning_RM  0.851793  0.841251
27         open_porch_sf   0.84967  0.840973
34           street_Pave  0.851675  0.840791
28     ms_zoning_C (all)  0.849693  0.840668
31          ms_zoning_RH  0.849849  0.839839
26          wood_deck_sf  0.848119  0.839663
30     ms_zoning_I (all)  0.848796  0.839051
38      land_contour_Lvl  0.851107  0.838831
39    lot_config_CulDSac  0.851253  0.838647
41        lot_config_FR3  0.851803   0.83856
25           garage_cond  0.846675  0.838472
42     lot_config_Inside  0.851945   0.83837
29          ms_zoning_FV  0.847792  0.838318
43  neighborhood_Blueste  0.852052  0.838142
40        lot_config_FR2  0.850662  0.837662
24           garage_qual   0.84528  0.837337
44   neighborhood_BrDale  0.851393  0.837074
45  neighborhood_BrkSide  0.851188  0.836499
48  neighborhood_Crawfor  0.851932  0.836262
49  neighborhood_Edwards  0.852084  0.836076
47  neighborhood_CollgCr  0.851425  0.836055
46  neighborhood_ClearCr  0.851063  0.836009
50  neighborhood_Gilbert  0.852161  0.835806
51   neighborhood_Greens   0.85207  0.835347
52  neighborhood_GrnHill  0.851734  0.834614
53   neighborhood_IDOTRR  0.851416  0.833898
22         garage_finish  0.841279  0.833813
23           garage_area  0.841392  0.833591
54  neighborhood_Landmrk  0.851343  0.833452
57    neighborhood_NAmes  0.851932  0.833016
55  neighborhood_MeadowV  0.851269  0.833004
56  neighborhood_Mitchel  0.851508  0.832905
59   neighborhood_NWAmes  0.852243   0.83263
58  neighborhood_NPkVill  0.851793   0.83249
60  neighborhood_NoRidge  0.852344  0.832373
61  neighborhood_NridgHt  0.852375  0.832035
62  neighborhood_OldTown  0.852424  0.831718
63    neighborhood_SWISU  0.852315  0.831218
64   neighborhood_Sawyer  0.852251  0.830766
21          fireplace_qu   0.83802  0.830747
65  neighborhood_SawyerW  0.852398  0.830555
66  neighborhood_Somerst  0.852421  0.830201
20             half_bath  0.837005  0.830033
19             full_bath  0.836441  0.829792
67  neighborhood_StoneBr  0.852221  0.829589
68   neighborhood_Timber  0.852165  0.829139
69  neighborhood_Veenker  0.852336   0.82895
70     condition_1_Feedr  0.852295  0.828515
71      condition_1_Norm  0.852214  0.828031
72      condition_1_PosA  0.852238  0.827667
17           gr_liv_area  0.833473  0.827405
73      condition_1_PosN    0.8522  0.827229
18        bsmt_full_bath  0.833389  0.826968
74      condition_1_RRAe  0.852067  0.826678
75      condition_1_RRAn  0.852146  0.826373
76      condition_1_RRNe   0.85224  0.826085
77      condition_1_RRNn  0.852276  0.825727
15            1st_flr_sf  0.830905  0.825451
78     condition_2_Feedr  0.852186  0.825218
79      condition_2_Norm  0.852158   0.82478
80      condition_2_PosA    0.8522  0.824423
81      condition_2_PosN  0.852205  0.824021
82      condition_2_RRAe  0.852232  0.823643
83      condition_2_RRAn  0.852235  0.823235
84      condition_2_RRNn  0.852233  0.822818
85      bldg_type_2fmCon  0.852242  0.822413
14            electrical  0.827551  0.822346
12        bsmtfin_type_1  0.826628  0.822111
86      bldg_type_Duplex  0.852242  0.821995
13            heating_qc  0.826573  0.821698
87       bldg_type_Twnhs  0.852242  0.821575
88      bldg_type_TwnhsE  0.852242  0.821153
16            2nd_flr_sf   0.82707  0.821131
89    house_style_1.5Unf  0.852242  0.820729
90    house_style_1Story  0.852242  0.820304
91    house_style_2.5Fin  0.852242  0.819876
92    house_style_2.5Unf  0.852241  0.819445
93    house_style_2Story  0.852241  0.819013
94    house_style_SFoyer  0.852241  0.818579
95      house_style_SLvl  0.852241  0.818142
96      roof_style_Gable  0.852241  0.817704
11         bsmt_exposure  0.821682  0.817402
97    roof_style_Gambrel  0.852241  0.817264
98        roof_style_Hip  0.852242  0.816823
99    roof_style_M

We calculate the adjusted $R^2$ on our test sets after training on our training sets. We find that 36 features give us the best adjusted $R^2$ score at 0.841979. We will use these 36 features to create our baseline model.<br/>
It is likely that more than 36 features cause model overfitting thereby giving us worse adjusted R-squared scores as compared to scoring on the training set. 

---
### Baseline Model <a id=linreg></a>

In [181]:
#We reduce our feature list down to 36 features
var36=var100[0:36]
len(var36)

36

In [183]:
#We create feature dataframes which only include our 36 features
X_scaled_36=X_scaled_df[var36]
X_sctest_36=X_sctest_df[var36]
print(X_scaled_36.shape)
print(X_sctest_36.shape)

(1538, 36)
(513, 36)


In [220]:
#We train our baseline model with our training data and score it to our test data 
lr = LinearRegression(fit_intercept=True,n_jobs=-1)
lr.fit(X_scaled_36, y_train)
r2=lr.score(X_sctest_36, y_test) #R-squared for linear regression
n=len(X_sctest_36)
i=36
print('r2: ' + str(r2))
print('adj R2: ' + str(1-(1-r2)*((n-1)/(n-i-1))))

r2: 0.8530608126922685
adj R2: 0.8419477649126922


We observe that using multiple linear regression as our baseline model gives us similar results to the lasso method above.<br/>
We reduce our feature list down to 'gr_liv_area' which has a correlation score of 0.7 with sale_price and observe the changes.

In [185]:
#Reduce feature list down to a single feature
var1=var100[0:1]
len(var1)

1

In [186]:
#We create feature dataframes which only have 'gr_liv_area'
X_scaled_1=X_scaled_df[var1]
X_sctest_1=X_sctest_df[var1]
print(X_scaled_1.shape)
print(X_sctest_1.shape)

(1538, 1)
(513, 1)


In [221]:
#We train our baseline model with our training data and score it to our test data 
lr.fit(X_scaled_1, y_train)
r2=lr.score(X_sctest_1, y_test) #R-squared for linear regression
n=len(X_sctest_1)
i=1
print('r2: ' + str(r2))
print('adj R2: ' + str(1-(1-r2)*((n-1)/(n-i-1))))

r2: 0.4194948514551927
adj R2: 0.4183588335519739


Our adjusted $R^2$ score becomes substantially worse.<br/>
In the next section, we try all three regularization methods with our 36 features to attempt to improve the model.

---
### Regularization <a id=reg></a>

#### Ridge Regularization<a id=ridge></a>
We run RidgeCV with our training data with 36 features over a range of parameters to obtain the optimal alpha parameter.

In [210]:
ridge_alphas = np.logspace(0, 5, 200)
optimal_ridge = RidgeCV(alphas=ridge_alphas, cv=10)

optimal_ridge.fit(X_scaled_36, y_train)

print(optimal_ridge.alpha_)

28.660676169482517


We then predict our target with our optimal alpha on our test dataset.

In [211]:
pred=optimal_ridge.predict(X_sctest_36)
r2=r2_score(y_test, pred)
n=len(X_sctest_36)
i=36
print('r2: ' + str(r2))
print('adj R2: ' + str(1-(1-r2)*((n-1)/(n-i-1))))

#enable the below command to plot out a bar graph of our coefficients
# pd.Series(optimal_ridge.coef_).plot.bar(figsize=(15, 7)) 

r2: 0.8537392185022317
adj R2: 0.8426774787250895


We observe that our model performs better than both our baseline and lasso models.<br/><br/>
Next, we try performing ridge regression on different combinations of features and observe if our model improves.

In [205]:
#We find a general optimal alpha using all features in our training set
ridge_alphas = np.logspace(0, 5, 200)
optimal_ridge = RidgeCV(alphas=ridge_alphas, cv=10)

optimal_ridge.fit(X_scaled, y_train)

print(optimal_ridge.alpha_)

289.9422853882878


In [206]:
#We create two lists to store r2 and adjusted r2 values for different combinations of features
ridge=Ridge(alpha=optimal_ridge.alpha_, fit_intercept=True, normalize=False)
ridger2=[]
ridgear2=[]
n=len(X_sctest_df)
for i in range(1,101):
    ridge.fit(X_scaled_df[var100[0:i]].values,y_train)
    r2=ridge.score(X_sctest_df[var100[0:i]].values,y_test)
    ridger2.append(r2)
    ridgear2.append(1-(1-r2)*((n-1)/(n-i-1)))

In [208]:
#We sort a dataframe of adjusted r2 values based on combinations of features 
ridgedf=pd.DataFrame([list(X_train.columns.values)[0:100],ridger2,ridgear2])
ridgedf.T.sort_values(2,ascending=False)

0         1         2
37      land_contour_Low  0.853927  0.842217
36      land_contour_HLS  0.853563  0.842156
27         open_porch_sf  0.850535  0.841888
32          ms_zoning_RL  0.852032  0.841838
28     ms_zoning_C (all)  0.850599  0.841629
35            alley_Pave  0.852686  0.841545
33          ms_zoning_RM   0.85191  0.841376
31          ms_zoning_RH  0.850682  0.840727
34           street_Pave  0.851572  0.840681
26          wood_deck_sf   0.84868  0.840256
30     ms_zoning_I (all)  0.849359   0.83965
25           garage_cond   0.84685  0.838657
29          ms_zoning_FV  0.848024  0.838565
24           garage_qual  0.844965  0.837006
41        lot_config_FR3  0.848055  0.834477
42     lot_config_Inside   0.84835  0.834446
43  neighborhood_Blueste  0.848523  0.834281
22         garage_finish    0.8409  0.833417
23           garage_area  0.840868  0.833041
44   neighborhood_BrDale   0.84734   0.83263
39    lot_config_CulDSac  0.845534  0.832444
38      land_contour_Lvl  0.844723   0.83192
45  neighborhood_BrkSide   0.84694  0.831831
40        lot_config_FR2  0.844892   0.83139
21          fireplace_qu  0.837788  0.830505
20             half_bath  0.837001   0.83003
19             full_bath  0.836402  0.829752
46  neighborhood_ClearCr   0.84528  0.829642
49  neighborhood_Edwards  0.846103  0.829447
48  neighborhood_Crawfor  0.845675  0.829342
47  neighborhood_CollgCr  0.845261  0.829254
50  neighborhood_Gilbert  0.846144  0.829123
51   neighborhood_Greens  0.846163  0.828772
17           gr_liv_area  0.834378  0.828343
52  neighborhood_GrnHill  0.845796   0.82799
53   neighborhood_IDOTRR  0.845572  0.827364
18        bsmt_full_bath  0.833647  0.827236
54  neighborhood_Landmrk  0.845517  0.826925
57    neighborhood_NAmes  0.846453  0.826837
55  neighborhood_MeadowV  0.845477  0.826501
56  neighborhood_Mitchel  0.845731  0.826405
15            1st_flr_sf  0.831754  0.826327
59   neighborhood_NWAmes  0.846474  0.826094
58  neighborhood_NPkVill  0.846011  0.825956
60  neighborhood_NoRidge  0.846503  0.825742
61  neighborhood_NridgHt  0.846673  0.825548
62  neighborhood_OldTown   0.84687  0.825384
63    neighborhood_SWISU  0.846713  0.824815
64   neighborhood_Sawyer  0.846606  0.824301
65  neighborhood_SawyerW  0.846806  0.824137
66  neighborhood_Somerst   0.84673  0.823653
69  neighborhood_Veenker  0.847063  0.822842
67  neighborhood_StoneBr  0.846187   0.82263
70     condition_1_Feedr  0.847003  0.822371
68   neighborhood_Timber  0.846085  0.822112
12        bsmtfin_type_1  0.826567  0.822048
14            electrical  0.827179  0.821963
71      condition_1_Norm  0.846864  0.821806
13            heating_qc   0.82638  0.821499
72      condition_1_PosA  0.846762  0.821281
73      condition_1_PosN  0.846676  0.820772
16            2nd_flr_sf  0.826658  0.820705
82      condition_2_RRAe  0.849619  0.820525
81      condition_2_PosN  0.849155  0.820389
83      condition_2_RRAn  0.849652  0.820144
85      bldg_type_2fmCon  0.850213  0.819975
74      condition_1_RRAe  0.846309  0.819931
76      condition_1_RRNe  0.846812  0.819695
75      condition_1_RRAn  0.846377  0.819599
86      bldg_type_Duplex  0.850242  0.819586
84      condition_2_RRNn    0.8495  0.819541
77      condition_1_RRNn  0.846801  0.819268
87       bldg_type_Twnhs  0.850258   0.81918
88      bldg_type_TwnhsE  0.850262  0.818757
78     condition_2_Feedr   0.84657  0.818577
89    house_style_1.5Unf  0.850327  0.818406
79      condition_2_Norm  0.846604  0.818198
80      condition_2_PosA  0.846742   0.81794
90    house_style_1Story  0.850297  0.817938
91    house_style_2.5Fin  0.850299  0.817508
92    house_style_2.5Unf   0.85032  0.817098
93    house_style_2Story  0.850309  0.816646
11         bsmt_exposure  0.820804  0.816503
94    house_style_SFoyer  0.850463  0.816396
95      house_style_SLvl  0.850461  0.815952
96      roof_style_Gable  0.850316   0.81533
9              bsmt_qual  0.818714  0.815102
97    roof_style_Gambrel  0.850297   0.81486
10             bsm

We observe that there is little change in the adjusted $R^2$ score. <br/>However, 37 features seem to be the best combination for ridge regression as compared to the 36 we obtained using the lasso method. <br/>The combination of 36 features seems to have a minimally lower adjusted $R^2$ as compared to the model earlier due to the change in the alpha used. 

---
#### Elastic Net Regularization<a id=enet></a>
We run ElasticNetCV with our training data with 36 features over a range of parameters to obtain the optimal alpha and l1 ratio.

In [218]:
l1_ratios = np.linspace(0.01, 1.0, 25)

optimal_enet = ElasticNetCV(l1_ratio=l1_ratios, n_alphas=100, cv=10,verbose=1,n_jobs=-1)
optimal_enet.fit(X_scaled_36, y_train)

print(optimal_enet.alpha_)
print(optimal_enet.l1_ratio_)

[Parallel(n_jobs=-1)]: Using backend ThreadingBackend with 8 concurrent workers.
.......................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................

63.74968209452979
1.0


We then predict our target with our optimal alpha and l1 ratio on our test dataset.

In [219]:
enet = ElasticNet(alpha=optimal_enet.alpha_, l1_ratio=optimal_enet.l1_ratio_)
enet.fit(X_scaled_36,y_train)
pred=enet.predict(X_sctest_36)
r2=r2_score(y_test, pred)
n=len(X_sctest_36)
i=36
print('r2: ' + str(r2))
print('adj R2: ' + str(1-(1-r2)*((n-1)/(n-i-1))))

r2: 0.8531491293048055
adj R2: 0.8420427609329


We observe that our model performs better than our baseline and lasso model and slightly worse than the ridge.<br/><br/>
Next, we try performing elastic net regression on different combinations of features and observe if our model improves.

In [222]:
#We find optimal alpha and l1 ratios by fitting to all our X training features
l1_ratios = np.linspace(0.01, 1.0, 25)

optimal_enet = ElasticNetCV(l1_ratio=l1_ratios, n_alphas=100, cv=10,verbose=1,n_jobs=-1)
optimal_enet.fit(X_scaled, y_train)

print(optimal_enet.alpha_)
print(optimal_enet.l1_ratio_)

[Parallel(n_jobs=-1)]: Using backend ThreadingBackend with 8 concurrent workers.
.......................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................

594.5316688409972
1.0


.......................................................[Parallel(n_jobs=-1)]: Done 250 out of 250 | elapsed:    6.3s finished


In [223]:
#We create two lists to store r2 and adjusted r2 values for different combinations of features
enetr2=[]
enetar2=[]
n=len(X_sctest_df)
for i in range(1,101):
    enet.fit(X_scaled_df[var100[0:i]].values,y_train)
    r2=enet.score(X_sctest_df[var100[0:i]].values,y_test)
    enetr2.append(r2)
    enetar2.append(1-(1-r2)*((n-1)/(n-i-1)))

In [224]:
#We sort a dataframe of adjusted r2 values based on combinations of features 
enetdf=pd.DataFrame([list(X_train.columns.values)[0:100],enetr2,enetar2])
enetdf.T.sort_values(2,ascending=False)

0         1         2
32          ms_zoning_RL  0.852874  0.842738
36      land_contour_HLS  0.853693  0.842297
37      land_contour_Low  0.853995   0.84229
33          ms_zoning_RM  0.852688   0.84221
35            alley_Pave  0.853149  0.842043
34           street_Pave  0.852127  0.841277
27         open_porch_sf  0.849625  0.840926
28     ms_zoning_C (all)   0.84937  0.840326
31          ms_zoning_RH  0.849826  0.839814
26          wood_deck_sf  0.847709   0.83923
38      land_contour_Lvl  0.851413  0.839161
39    lot_config_CulDSac  0.851514   0.83893
41        lot_config_FR3  0.852053  0.838832
42     lot_config_Inside  0.852287  0.838744
30     ms_zoning_I (all)  0.848459  0.838693
43  neighborhood_Blueste  0.852453  0.838581
25           garage_cond  0.846325  0.838104
29          ms_zoning_FV  0.847243  0.837736
40        lot_config_FR2    0.8504  0.837378
24           garage_qual  0.845023  0.837067
48  neighborhood_Crawfor  0.852521  0.836913
49  neighborhood_Edwards  0.852789  0.836857
44   neighborhood_BrDale  0.851178  0.836837
50  neighborhood_Gilbert  0.852742  0.836451
45  neighborhood_BrkSide  0.850868  0.836146
47  neighborhood_CollgCr  0.851474  0.836109
51   neighborhood_Greens  0.852631  0.835972
46  neighborhood_ClearCr   0.85095  0.835885
52  neighborhood_GrnHill   0.85158  0.834442
53   neighborhood_IDOTRR  0.850692  0.833088
22         garage_finish  0.840582  0.833084
23           garage_area  0.840667   0.83283
54  neighborhood_Landmrk  0.850612  0.832633
57    neighborhood_NAmes  0.851423  0.832442
55  neighborhood_MeadowV  0.850438  0.832071
56  neighborhood_Mitchel  0.850719  0.832017
59   neighborhood_NWAmes  0.851139  0.831379
60  neighborhood_NoRidge  0.851279  0.831164
61  neighborhood_NridgHt  0.851304  0.830817
58  neighborhood_NPkVill  0.850311  0.830815
62  neighborhood_OldTown  0.851409   0.83056
21          fireplace_qu  0.837356  0.830054
63    neighborhood_SWISU  0.851054  0.829776
20             half_bath  0.836323  0.829323
65  neighborhood_SawyerW  0.851192  0.829172
64   neighborhood_Sawyer  0.850833  0.829142
19             full_bath  0.835711  0.829033
66  neighborhood_Somerst  0.851248  0.828851
67  neighborhood_StoneBr  0.850326  0.827403
69  neighborhood_Veenker  0.850774  0.827141
68   neighborhood_Timber  0.850071  0.826719
17           gr_liv_area  0.832511  0.826408
70     condition_1_Feedr  0.850452  0.826375
18        bsmt_full_bath  0.832207   0.82574
71      condition_1_Norm  0.850207  0.825696
72      condition_1_PosA  0.850246  0.825344
73      condition_1_PosN   0.85017  0.824856
15            1st_flr_sf  0.829906  0.824419
74      condition_1_RRAe   0.84949  0.823659
75      condition_1_RRAn  0.849668  0.823463
76      condition_1_RRNe  0.849772   0.82318
77      condition_1_RRNn  0.849879  0.822899
78     condition_2_Feedr  0.849439   0.82197
14            electrical  0.827002  0.821781
12        bsmtfin_type_1  0.826243  0.821716
79      condition_2_Norm  0.849425   0.82154
85      bldg_type_2fmCon  0.851452  0.821463
81      condition_2_PosN  0.849912  0.821291
80      condition_2_PosA  0.849554   0.82128
13            heating_qc  0.826092  0.821203
82      condition_2_RRAe  0.850132  0.821137
86      bldg_type_Duplex  0.851503  0.821105
83      condition_2_RRAn  0.850188  0.820786
84      condition_2_RRNn  0.849945  0.820075
16            2nd_flr_sf  0.825871  0.819891
87       bldg_type_Twnhs  0.850595  0.819587
88      bldg_type_TwnhsE  0.850599  0.819165
89    house_style_1.5Unf  0.850718   0.81888
90    house_style_1Story  0.850717   0.81845
91    house_style_2.5Fin  0.850698  0.817993
92    house_style_2.5Unf  0.850811  0.817697
93    house_style_2Story  0.850809  0.817259
94    house_style_SFoyer  0.850792    0.8168
11         bsmt_exposure  0.820706  0.816402
95      house_style_SLvl  0.850716  0.816266
96      roof_style_Gable   0.85055  0.815618
97    roof_style_Gambrel   0.85047  0.815074
10             bsmt_cond  0.818458  0.814472
98        roof_sty

So far, it seems that elastic net regression yields the best adjusted $R^2$ values amongst the models we have tried.<br/>
For a combination of 32 features, we can obtain an adjusted $R^2$ value of 0.8427 using an alpha which was not even optimized for 32 features.<br/>
We can attempt to optimize the model for 32 features to observe if there will be any improvement.

---
# Final Model<a id=finalmodel></a>
### Summary<a id=summary></a>
The summary of the scoring of the models we have created so far is given below in a table form:

|Method|Number of Features|Parameters Optimized over|Parameter value|Adjusted $R^2$ score|
|---|---|---|---|---|
|Lasso|36|All features|568.038|0.841979|
|Linear Regression|36|NA|NA|0.841947|
|Linear Regression|1|NA|NA|0.418358|
|Ridge|36|36 features|28.660|0.842677|
|Ridge|37|All features|289.942|0.842217|
|Elastic Net|36|36 features|$\alpha=63.749$, $l_1 ratio=1.0$|0.842042|
|Elastic Net|32|All features|$\alpha=594.531$, $l_1 ratio=1.0$|0.842738|

The best model we have created is for a combination of 32 features using elastic net regression.<br/>
For our final model, we shall optimize elastic net for 32 features by finding the optimum parameters for 32 features.<br/><br/>
### Final Model<a id=finmod></a>
We run ElasticNetCV with our training data with 32 features over a range of parameters to obtain the optimal alpha and l1 ratio.

In [225]:
l1_ratios = np.linspace(0.01, 1.0, 25)

optimal_enet = ElasticNetCV(l1_ratio=l1_ratios, n_alphas=100, cv=10,verbose=1,n_jobs=-1)
optimal_enet.fit(X_scaled_df[var100[0:32]].values, y_train)

print(optimal_enet.alpha_)
print(optimal_enet.l1_ratio_)

[Parallel(n_jobs=-1)]: Using backend ThreadingBackend with 8 concurrent workers.
.......................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................

240.01346078933193
1.0


....[Parallel(n_jobs=-1)]: Done 250 out of 250 | elapsed:    5.5s finished


We then predict our target with our optimal alpha and l1 ratio on our test dataset.

In [227]:
enet = ElasticNet(alpha=optimal_enet.alpha_, l1_ratio=optimal_enet.l1_ratio_)
enet.fit(X_scaled_df[var100[0:32]].values,y_train)
r2=enet.score(X_sctest_df[var100[0:32]].values,y_test)
n=len(X_sctest_df[var100[0:32]])
i=32
print('r2: ' + str(r2))
print('adj R2: ' + str(1-(1-r2)*((n-1)/(n-i-1))))

r2: 0.8500401550381356
adj R2: 0.840042832040678


This model has an adjusted $R^2$ score which is worse compared to the model with parameters optimized over all features.<br/>
As such, for our final model, we will be using an Elastic Net Regression method, with parameters of $\alpha=594.531$ and $l_1 ratio=1.0$ to predict our sales prices from a combination of the first 32 features listed in the var100 list.

---
Before we carry on, we export all useful information related to our model.

In [229]:
#We export the optimal Elastic Net alpha and l1 ratio externally
l1_ratios = np.linspace(0.01, 1.0, 25)

optimal_enet = ElasticNetCV(l1_ratio=l1_ratios, n_alphas=100, cv=10,verbose=1,n_jobs=-1)
optimal_enet.fit(X_scaled, y_train)

alpha=optimal_enet.alpha_
l1=optimal_enet.l1_ratio_

[Parallel(n_jobs=-1)]: Using backend ThreadingBackend with 8 concurrent workers.
.......................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................................

In [230]:
f= open(r"..\datasets\enet.txt","w+")
f.write("alpha = " + str(alpha) + ' , l1 ratio = ' + str(l1))
f.close()

In [277]:
#We export our final list of features externally
var32=var100[0:32]
np.savetxt(r'..\datasets\features.txt',var32,fmt='%s')

---
# Prediction<a id=predict></a>

### Import and Cleaning <a id=predimp></a>
First, we import and clean our test dataset.

In [305]:
df=pd.read_csv(r'..\datasets\test.csv',index_col='Id')
df.head()

PID  MS SubClass MS Zoning  Lot Frontage  Lot Area Street Alley  \
Id                                                                            
2658  902301120          190        RM          69.0      9142   Pave  Grvl   
2718  905108090           90        RL           NaN      9662   Pave   NaN   
2414  528218130           60        RL          58.0     17104   Pave   NaN   
1989  902207150           30        RM          60.0      8520   Pave   NaN   
625   535105100           20        RL           NaN      9500   Pave   NaN   

     Lot Shape Land Contour Utilities Lot Config Land Slope Neighborhood  \
Id                                                                         
2658       Reg          Lvl    AllPub     Inside        Gtl      OldTown   
2718       IR1          Lvl    AllPub     Inside        Gtl       Sawyer   
2414       IR1          Lvl    AllPub     Inside        Gtl      Gilbert   
1989       Reg          Lvl    AllPub     Inside        Gtl      OldTown   
625        IR1          Lvl    AllPub     Inside        Gtl        NAmes   

     Condition 1 Condition 2 Bldg Type House Style  Overall Qual  \
Id                                                                 
2658        Norm        Norm    2fmCon      2Story             6   
2718        Norm        Norm    Duplex      1Story             5   
2414        Norm        Norm      1Fam      2Story             7   
1989        Norm        Norm      1Fam      1Story             5   
625         Norm        Norm      1Fam      1Story             6   

      Overall Cond  Year Built  Year Remod/Add Roof Style Roof Matl  \
Id                                                                    
2658             8        1910            1950      Gable   CompShg   
2718             4        1977            1977      Gable   CompShg   
2414             5        2006            2006      Gable   CompShg   
1989             6        1923            2006      Gable   CompShg   
625              5        1963            1963      Gable   CompShg   

     Exterior 1st Exterior 2nd Mas Vnr Type  Mas Vnr Area Exter Qual  \
Id                                                                     
2658      AsbShng      AsbShng         None           0.0         TA   
2718      Plywood      Plywood         None           0.0         TA   
2414      VinylSd      VinylSd         None           0.0         Gd   
1989      Wd Sdng      Wd Sdng         None           0.0         Gd   
625       Plywood      Plywood      BrkFace         247.0         TA   

     Exter Cond Foundation Bsmt Qual Bsmt Cond Bsmt Exposure BsmtFin Type 1  \
Id                                                                            
2658         Fa      Stone        Fa        TA            No            Unf   
2718         TA     CBlock        Gd        TA            No            Unf   
2414         TA      PConc        Gd        Gd            Av            GLQ   
1989         TA     CBlock        TA        TA            No            Unf   
625          TA     CBlock        Gd        TA            No            BLQ   

      BsmtFin SF 1 BsmtFin Type 2  BsmtFin SF 2  Bsmt Unf SF  Total Bsmt SF  \
Id                                                                            
2658             0            Unf             0         1020           1020   
2718             0            Unf             0         1967           1967   
2414           554            Unf             0          100            654   
1989             0            Unf             0          968            968   
625            609            Unf             0          785           1394   

     Heating Heating QC Central Air Electrical  1st Flr SF  2nd Flr SF  \
Id                                                                       
2658    GasA         Gd           N      FuseP         908        1020   
2718    GasA         TA           Y      SBrkr        1967           0   
2414    GasA         Ex           Y      

In [306]:
#remove all NaN values
fill_zeroes(df)
df.isna().sum()

PID                0
MS SubClass        0
MS Zoning          0
Lot Frontage       0
Lot Area           0
Street             0
Alley              0
Lot Shape          0
Land Contour       0
Utilities          0
Lot Config         0
Land Slope         0
Neighborhood       0
Condition 1        0
Condition 2        0
Bldg Type          0
House Style        0
Overall Qual       0
Overall Cond       0
Year Built         0
Year Remod/Add     0
Roof Style         0
Roof Matl          0
Exterior 1st       0
Exterior 2nd       0
Mas Vnr Type       0
Mas Vnr Area       0
Exter Qual         0
Exter Cond         0
Foundation         0
Bsmt Qual          0
Bsmt Cond          0
Bsmt Exposure      0
BsmtFin Type 1     0
BsmtFin SF 1       0
BsmtFin Type 2     0
BsmtFin SF 2       0
Bsmt Unf SF        0
Total Bsmt SF      0
Heating            0
Heating QC         0
Central Air        0
Electrical         1
1st Flr SF         0
2nd Flr SF         0
Low Qual Fin SF    0
Gr Liv Area        0
Bsmt Full Bat

In [307]:
#convert all necesssary data
data_conv(df)

In [308]:
#check datatypes of converted ordinal data
df[['Lot Shape','Utilities','Land Slope','Exter Qual',\
    'Exter Cond','Bsmt Qual','Bsmt Exposure','BsmtFin Type 1',\
    'BsmtFin Type 2','Heating QC','Electrical','Kitchen Qual',\
    'Functional','Fireplace Qu','Garage Finish','Garage Qual',\
    'Garage Cond','Paved Drive','Pool QC','Fence']].info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 879 entries, 2658 to 1939
Data columns (total 20 columns):
Lot Shape         879 non-null int64
Utilities         879 non-null object
Land Slope        879 non-null int64
Exter Qual        879 non-null object
Exter Cond        879 non-null int64
Bsmt Qual         879 non-null int64
Bsmt Exposure     879 non-null int64
BsmtFin Type 1    879 non-null int64
BsmtFin Type 2    879 non-null int64
Heating QC        879 non-null object
Electrical        878 non-null object
Kitchen Qual      879 non-null int64
Functional        879 non-null object
Fireplace Qu      879 non-null object
Garage Finish     879 non-null int64
Garage Qual       879 non-null int64
Garage Cond       879 non-null int64
Paved Drive       879 non-null int64
Pool QC           879 non-null int64
Fence             879 non-null int64
dtypes: int64(14), object(6)
memory usage: 144.2+ KB


In [309]:
#check unique values of problematic datatypes
display(np.unique(df['Utilities'],return_counts=True))
display(np.unique(df['Exter Qual'],return_counts=True))
display(np.unique(df['Heating QC'],return_counts=True))
display(np.unique(df['Electrical'],return_counts=True))
display(np.unique(df['Functional'],return_counts=True))
display(np.unique(df['Fireplace Qu'],return_counts=True))

(array([2, 3], dtype=object), array([  1, 878], dtype=int64))

(array([1, 2, 3, 4], dtype=object), array([  9, 552, 292,  26], dtype=int64))

(array([1, 2, 3, 4], dtype=object), array([ 25, 267, 157, 430], dtype=int64))

(array([1, 2, nan, 2, 3, 4], dtype=object),
 array([  1,   9,   1,   6,  48, 814], dtype=int64))

(array([2, 3, 4, 5, 6, 7], dtype=object),
 array([  2,   7,   6,  28,  23, 813], dtype=int64))

(array([0, 1, 2, 3, 4, 5], dtype=object),
 array([422,  15,  16, 193, 221,  12], dtype=int64))

In [310]:
#identify NaN values in 'Electrical'
df[['Electrical']].isna().sum()

Electrical    1
dtype: int64

In [311]:
#Find the most appropriate value to fill NA
df[['Electrical']].mode()

Electrical
0          4

In [312]:
#We fill with the mode of 4
df.fillna(value={'Electrical':4},inplace=True)

The six features of 'Utilities', 'Exter Qual', 'Heating QC', 'Electrical', 'Functional' and 'Fireplace Qu' are given as dtype objects even though the values are all integers.<br/> 
We shall convert these features to dtype int.

In [313]:
#Convert the faulty datatypes
df[['Utilities','Exter Qual','Heating QC', 'Electrical', 'Functional','Fireplace Qu']]=df[['Utilities','Exter Qual','Heating QC', 'Electrical', 'Functional','Fireplace Qu']].astype(int)

In [314]:
#Check that conversion was succesful
df[['Utilities','Exter Qual','Heating QC', 'Electrical', 'Functional','Fireplace Qu']].info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 879 entries, 2658 to 1939
Data columns (total 6 columns):
Utilities       879 non-null int32
Exter Qual      879 non-null int32
Heating QC      879 non-null int32
Electrical      879 non-null int32
Functional      879 non-null int32
Fireplace Qu    879 non-null int32
dtypes: int32(6)
memory usage: 27.5 KB


In [315]:
#change feature names and drop PID
df.columns=map(str.lower,df.columns)
df.columns=df.columns.str.replace(' ','_')
df.drop('pid',axis=1,inplace=True)
df.columns

Index(['ms_subclass', 'ms_zoning', 'lot_frontage', 'lot_area', 'street',
       'alley', 'lot_shape', 'land_contour', 'utilities', 'lot_config',
       'land_slope', 'neighborhood', 'condition_1', 'condition_2', 'bldg_type',
       'house_style', 'overall_qual', 'overall_cond', 'year_built',
       'year_remod/add', 'roof_style', 'roof_matl', 'exterior_1st',
       'exterior_2nd', 'mas_vnr_type', 'mas_vnr_area', 'exter_qual',
       'exter_cond', 'foundation', 'bsmt_qual', 'bsmt_cond', 'bsmt_exposure',
       'bsmtfin_type_1', 'bsmtfin_sf_1', 'bsmtfin_type_2', 'bsmtfin_sf_2',
       'bsmt_unf_sf', 'total_bsmt_sf', 'heating', 'heating_qc', 'central_air',
       'electrical', '1st_flr_sf', '2nd_flr_sf', 'low_qual_fin_sf',
       'gr_liv_area', 'bsmt_full_bath', 'bsmt_half_bath', 'full_bath',
       'half_bath', 'bedroom_abvgr', 'kitchen_abvgr', 'kitchen_qual',
       'totrms_abvgrd', 'functional', 'fireplaces', 'fireplace_qu',
       'garage_type', 'garage_yr_blt', 'garage_finish', 'gara

In [316]:
df.to_csv(r'..\datasets\test_cleaned.csv')

### Dummies <a id=predummies></a>
Then we drop features and create our dummy features.

In [318]:
df=pd.read_csv(r'..\datasets\test_cleaned.csv',index_col='Id')

In [319]:
# Create dummies
df_dummies = pd.get_dummies(df, drop_first=True)
df.head()

ms_subclass ms_zoning  lot_frontage  lot_area street alley  lot_shape  \
Id                                                                            
2658          190        RM          69.0      9142   Pave  Grvl          3   
2718           90        RL          69.0      9662   Pave   NaN          2   
2414           60        RL          58.0     17104   Pave   NaN          2   
1989           30        RM          60.0      8520   Pave   NaN          3   
625            20        RL          69.0      9500   Pave   NaN          2   

     land_contour  utilities lot_config  land_slope neighborhood condition_1  \
Id                                                                             
2658          Lvl          3     Inside           2      OldTown        Norm   
2718          Lvl          3     Inside           2       Sawyer        Norm   
2414          Lvl          3     Inside           2      Gilbert        Norm   
1989          Lvl          3     Inside           2      OldTown        Norm   
625           Lvl          3     Inside           2        NAmes        Norm   

     condition_2 bldg_type house_style  overall_qual  overall_cond  \
Id                                                                   
2658        Norm    2fmCon      2Story             6             8   
2718        Norm    Duplex      1Story             5             4   
2414        Norm      1Fam      2Story             7             5   
1989        Norm      1Fam      1Story             5             6   
625         Norm      1Fam      1Story             6             5   

      year_built  year_remod/add roof_style roof_matl exterior_1st  \
Id                                                                   
2658        1910            1950      Gable   CompShg      AsbShng   
2718        1977            1977      Gable   CompShg      Plywood   
2414        2006            2006      Gable   CompShg      VinylSd   
1989        1923            2006      Gable   CompShg      Wd Sdng   
625         1963            1963      Gable   CompShg      Plywood   

     exterior_2nd mas_vnr_type  mas_vnr_area  exter_qual  exter_cond  \
Id                                                                     
2658      AsbShng         None           0.0           2           1   
2718      Plywood         None           0.0           2           2   
2414      VinylSd         None           0.0           3           2   
1989      Wd Sdng         None           0.0           3           2   
625       Plywood      BrkFace         247.0           2           2   

     foundation  bsmt_qual  bsmt_cond  bsmt_exposure  bsmtfin_type_1  \
Id                                                                     
2658      Stone          2          3              1               1   
2718     CBlock          4          3              1               1   
2414      PConc          4          4              3               6   
1989     CBlock          3          3              1               1   
625      CBlock          4          3              1               4   

      bsmtfin_sf_1  bsmtfin_type_2  bsmtfin_sf_2  bsmt_unf_sf  total_bsmt_sf  \
Id                                                                             
2658             0               1             0         1020           1020   
2718             0               1             0         1967           1967   
2414           554               1             0          100            654   
1989             0               1             0          968            968   
625            609               1             0          785           1394   

     heating  heating_qc central_air  electrical  1st_flr_sf  2nd_flr_sf  \
Id                                                                         
2658    GasA           3           N           1         908        1020   
2718    GasA           2           Y           4        1967           0   
2414    GasA           4          

In [320]:
#export our dummified data
df_dummies.to_csv(r'..\datasets\test_drop_dummies.csv')

### Prediction <a id=pred></a>
First, we scale the data according to the parameters we obtained from [splitting and scaling](#splitscale).<br/>
Then, we use our Elastic Net Regression with the parameters we determined to predict our target values using the predetermined 32 features.

In [321]:
df_dummies=pd.read_csv(r'..\datasets\test_drop_dummies.csv',index_col='Id')

In [322]:
#Reduce our dataframe only to the required features
df_dummies=df_dummies[var32]

KeyError: "['neighborhood_GrnHill'] not in index"

In [323]:
#Add a feature of 0s to resolve the above error
df_dummies['neighborhood_GrnHill']=0

In [324]:
#Reduce our dataframe only to the required features
df_dummies=df_dummies[var32]

In [328]:
#Scale data to z-scores
ss.fit(X_train[var32])
X_test_scaled= ss.transform(df_dummies) #transform our data according to the fit obtained from the training set

E:\Users\chang\Anaconda3\lib\site-packages\sklearn\preprocessing\data.py:645: DataConversionWarning: Data with input dtype int64, float64 were all converted to float64 by StandardScaler.
  return self.partial_fit(X, y)
E:\Users\chang\Anaconda3\lib\site-packages\ipykernel_launcher.py:3: DataConversionWarning: Data with input dtype int64, float64 were all converted to float64 by StandardScaler.
  This is separate from the ipykernel package so we can avoid doing imports until


In [327]:
#check if we are using the right enet parameters
print(optimal_enet.alpha_)
print(optimal_enet.l1_ratio_)

594.5316688409972
1.0


In [329]:
#obtain our array of predicted sales prices
enet.fit(X_scaled_df[var32].values,y_train)
pred=enet.predict(X_test_scaled)
pred

array([130452.02340116, 154417.30123377, 236635.8219623 , 104106.63723122,
       178048.58928816,  81928.43710546, 107166.98560882, 151597.13006421,
       177264.24017038, 157146.26362804, 135391.21204476, 119595.90883502,
       158288.26176785, 285868.26566058, 158206.24980366, 124730.66877552,
       128700.92496934, 124558.28306765, 178755.86308324, 181939.83205814,
       158936.83909314, 132528.21564106, 170816.38260523, 170774.04974868,
       178364.54635934, 134245.79942847, 123139.64968145, 106867.19323645,
       163123.20046278,  46246.19953843, 105125.45799204, 100488.80805374,
       218713.98528231, 138902.08794732, 212497.46186525, 193852.93477523,
       117148.76719944,  84792.21639047, 131125.17952192, 197926.91288866,
       181492.03611713, 196548.90235464, 155801.16645169, 174510.50288447,
       205042.21022766,  92324.66165706, 230155.60806395, 121696.17758369,
       132354.47113873, 108406.74016725, 101270.37807543, 208507.80081091,
       246096.7823563 , 1

In [337]:
#create a dataframe of our house IDs and predicted sale prices
pred_df=pd.DataFrame(index=df_dummies.index,data=pred,columns=['SalePrice'])
pred_df.sort_values('Id',ascending=True,inplace=True)

In [342]:
#export our predictions for submission
pred_df.to_csv(r'..\datasets\prediction.csv')

---
# Postamble<a id=end></a>

Due to a lack of time, we were not able to do the following but they can be future areas of research and improvement for us:
- Run Recursive Feature Elimination with the full set of features instead of dropping any, to allow the algorithm to pick the best selection of features for our model.
- Try our modelling process taking the advice from the data dictionary to remove outliers where the houses' living area is above 4000 units.
- Run a grid search for hyperparameter tuning.

<br/>
In general, we have found that sale price prediction of houses in Ames is a complex mix of factors and our model accounts for up to 32 of them.<br/>
The most important features that affect house prices in Ames would be the above grade ground living area, the overall material and finish of the house, and the neighbourhood in which the house is located.